In [1]:
# https://www.kaggle.com/iafoss/pretrained-resnet34-with-rgby-0-460-public-lb
import torch
print(torch.__version__)

0.3.1


In [2]:
# 31072 * 4 + 298424

# 422712

# 422712/4 = 105678

In [3]:
from fastai.conv_learner import *
from fastai.dataset import *

import pandas as pd
import numpy as np
import os
from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score
import scipy.optimize as opt
from tqdm import tqdm_notebook, tqdm

In [4]:
PATH = './'
TRAIN = '../data/train_combined/'
TEST = '../data/test/'
LABELS = '../data/train_combined_all.csv'
SAMPLE = '../data/sample_submission.csv'

In [5]:
name_label_dict = {
0:  'Nucleoplasm',
1:  'Nuclear membrane',
2:  'Nucleoli',   
3:  'Nucleoli fibrillar center',
4:  'Nuclear speckles',
5:  'Nuclear bodies',
6:  'Endoplasmic reticulum',   
7:  'Golgi apparatus',
8:  'Peroxisomes',
9:  'Endosomes',
10:  'Lysosomes',
11:  'Intermediate filaments',
12:  'Actin filaments',
13:  'Focal adhesion sites',   
14:  'Microtubules',
15:  'Microtubule ends',  
16:  'Cytokinetic bridge',   
17:  'Mitotic spindle',
18:  'Microtubule organizing center',  
19:  'Centrosome',
20:  'Lipid droplets',
21:  'Plasma membrane',   
22:  'Cell junctions', 
23:  'Mitochondria',
24:  'Aggresome',
25:  'Cytosol',
26:  'Cytoplasmic bodies',   
27:  'Rods & rings' }

In [6]:
nw = 2   #number of workers for data loader
arch = resnet50 #specify target architecture

In [7]:
# train_names_png = list({f[:36] for f in os.listdir(TRAIN) if 'png' in f})
# train_names_jpg = []
# for f in tqdm_notebook(os.listdir(TRAIN)):
#     if 'png' in f:
#         continue
#     name = f.split('.')[0]
#     name = name.split('_')
#     if len(name) == 5:
#         name = name[0]+'_'+name[1]+'_'+name[2]+'_'+name[3]
#     else:
#         name = name[0]+'_'+name[1]+'_'+name[2]+'_'+name[3]+'_'+name[4]
#     if name not in train_names_jpg:
#         train_names_jpg.append(name)

# train_names = train_names_png + train_names_jpg
# test_names = list({f[:36] for f in os.listdir(TEST)})


# tr_n, val_n = train_test_split(train_names, test_size=0.1, random_state=42)

In [8]:
import pickle
with open('../cache/train_names', 'rb') as f:
    train_names = pickle.load(f)
print(len(train_names))
test_names = list({f[:36] for f in os.listdir(TEST)})
# tr_n, val_n = train_test_split(train_names, test_size=0.1, random_state=42)

105678


In [9]:
from sklearn.model_selection import KFold

indexes = np.arange(len(train_names))
np.random.shuffle(indexes)

n_splits = 5
# kf = KFold(n_splits=n_splits, random_state=42, shuffle=True)
# fold_ = 0
# train_indexes = []
# valid_indexes = []
# for tr, v in kf.split(indexes):
#     print(len(train_indexes), len(valid_indexes))
#     train_indexes.append(tr)
#     valid_indexes.append(v)

In [10]:
# import pickle
# with open('../cache/train_names', 'wb') as f:
#     pickle.dump(train_names, f)
# with open('../cache/train_names_png1', 'wb') as f:
#     pickle.dump(train_names_png, f)
# with open('../cache/train_names_png2', 'wb') as f:
#     pickle.dump(train_names_jpg, f)

In [11]:
# len(train_names), len(train_names_jpg), len(train_names_png)
# (105678, 74606, 31072)

In [12]:
def open_rgby(path,id): #a function that reads RGBY image
#     colors = ['red','green','blue','yellow']
    colors = ['red','green','blue']
    flags = cv2.IMREAD_GRAYSCALE
    img = [cv2.imread(os.path.join(path, id+'_'+color+'.png'), flags).astype(np.float32)/255
           for color in colors]
    return np.stack(img, axis=-1)

In [13]:
# ??FilesDataset

In [14]:
class pdFilesDataset(FilesDataset):
    def __init__(self, fnames, path, transform):
        self.labels = pd.read_csv(LABELS).set_index('Id')
        self.labels['Target'] = [[int(i) for i in s.split()] for s in self.labels['Target']]
#         print(fnames)
        super().__init__(fnames, transform, path)
    
    def get_x(self, i):
        img = open_rgby(self.path,self.fnames[i])
        if self.sz == 512: return img 
        else: return cv2.resize(img, (self.sz, self.sz),cv2.INTER_AREA)
    
    def get_y(self, i):
        if(self.path == TEST): return np.zeros(len(name_label_dict),dtype=np.int)
        else:
            labels = self.labels.loc[self.fnames[i]]['Target']
            return np.eye(len(name_label_dict),dtype=np.float)[labels].sum(axis=0)
        
    @property
    def is_multi(self): return True
    @property
    def is_reg(self):return True
    #this flag is set to remove the output sigmoid that allows log(sigmoid) optimization
    #of the numerical stability of the loss function
    
    def get_c(self): return len(name_label_dict) #number of classes

In [15]:
# ??tfms_from_stats
path_to_train = '../data/train_combined'
data = pd.read_csv('../data/train_combined_all.csv')

In [16]:
# np.save('../cache/train_indexes_59max', train_indexes)
# np.save('../cache/valid_indexes_59max', valid_indexes)

In [17]:
my_train_indexes = list(np.load('../cache/train_indexes_59max.npy'))
my_valid_indexes = list(np.load('../cache/valid_indexes_59max.npy'))

In [18]:
for train_indexes, valid_indexes in zip(my_train_indexes, my_valid_indexes):
    print(train_indexes, valid_indexes)

[     0      1      2 ... 105674 105675 105676] [     8     23     24 ... 105664 105670 105677]
[     0      2      3 ... 105675 105676 105677] [     1      6      7 ... 105650 105668 105673]
[     1      2      3 ... 105675 105676 105677] [     0      4     11 ... 105665 105666 105669]
[     0      1      2 ... 105673 105674 105677] [     3      9     10 ... 105671 105675 105676]
[     0      1      3 ... 105675 105676 105677] [     2      5     15 ... 105667 105672 105674]


In [19]:
class FocalLoss(nn.Module):
    def __init__(self, gamma=2):
        super().__init__()
        self.gamma = gamma
        
    def forward(self, input, target):
        if not (target.size() == input.size()):
            raise ValueError("Target size ({}) must be the same as input size ({})"
                             .format(target.size(), input.size()))

        max_val = (-input).clamp(min=0)
        loss = input - input * target + max_val + \
            ((-max_val).exp() + (-input - max_val).exp()).log()

        invprobs = F.logsigmoid(-input * (target * 2.0 - 1.0))
        loss = (invprobs * self.gamma).exp() * loss
        
        return loss.sum(dim=1).mean()

In [20]:
def acc(preds,targs,th=0.0):
    preds = (preds > th).int()
    targs = targs.int()
    return (preds==targs).float().mean()

In [21]:
def sigmoid_np(x):
    return 1.0/(1.0 + np.exp(-x))

In [22]:
def F1_soft(preds,targs,th=0.5,d=50.0):
    preds = sigmoid_np(d*(preds - th))
    targs = targs.astype(np.float)
    score = 2.0*(preds*targs).sum(axis=0)/((preds+targs).sum(axis=0) + 1e-6)
    return score

def fit_val(x,y):
    params = 0.5*np.ones(len(name_label_dict))
    wd = 1e-5
    error = lambda p: np.concatenate((F1_soft(x,y,p) - 1.0,
                                      wd*(p - 0.5)), axis=None)
    p, success = opt.leastsq(error, params)
    return p

In [23]:
submit = pd.read_csv('../data/sample_submission.csv')

# oof_class_preds = np.zeros((len(train_names), 28))
# sub_class_preds = np.zeros((submit.shape[0], 28))

# oof_class_preds = np.load('../cache/oof_class_preds-59.npy')
# sub_class_preds = np.load('../cache/sub_class_preds-59.npy')


In [24]:
# ??ImageData.get_ds

In [25]:

oof_class_preds = np.load('../cache/oof_class_preds-59.npy')
sub_class_preds = np.load('../cache/sub_class_preds-59.npy')

fold_ = 0
for train_indexes, valid_indexes in zip(my_train_indexes, my_valid_indexes):
    if fold_ != 4:
        fold_ += 1
        print(train_indexes, valid_indexes)
        continue
    print(train_indexes, valid_indexes)
    tr_n = [train_names[i] for i in train_indexes]
    val_n = [train_names[i] for i in valid_indexes]
    
    def get_data(sz,bs):
        #data augmentation
        aug_tfms = [RandomRotate(30, tfm_y=TfmType.NO),
                    RandomDihedral(tfm_y=TfmType.NO),
                    RandomLighting(0.05, 0.05, tfm_y=TfmType.NO)]
        #mean and std in of each channel in the train set
    #     stats = A([0.08069, 0.05258, 0.05487, 0.08282], [0.13704, 0.10145, 0.15313, 0.13814])
    #     stats = A([0.08069, 0.05258, 0.05487], [0.13704, 0.10145, 0.15313])
        stats = A([0.0751 , 0.05909, 0.04364], [0.11428, 0.09856, 0.09925])
        tfms = tfms_from_stats(stats, sz, crop_type=CropType.NO, tfm_y=TfmType.NO, 
                    aug_tfms=aug_tfms)
        ds = ImageData.get_ds(pdFilesDataset, (tr_n[:-(len(tr_n)%bs)],TRAIN), 
                    (val_n,TRAIN), tfms, test=(test_names,TEST))
        md = ImageData(PATH, ds, bs, num_workers=nw, classes=None)
        return md
    
    bs = 16
    sz = 512
    md = get_data(sz,bs)

    learner = ConvLearner.pretrained(arch, md, ps=0.5) #dropout 50%
    learner.opt_fn = optim.Adam
    learner.clip = 1.0 #gradient clipping
    learner.crit = FocalLoss()
    learner.metrics = [acc]
    
    lr = 8e-4
    learner.fit(lr,1)
    name = 'ResNet50_512_59Max-{}-0'.format(fold_)
    learner.save(name)
    
    learner.unfreeze()
    lrs=np.array([lr/10,lr/3,lr])
    
    learner.fit(lrs/4,4,cycle_len=2,use_clr=(10,20))
    name = 'ResNet50_512_59Max-{}-1'.format(fold_)
    learner.save(name)
    
    learner.fit(lrs/4,2,cycle_len=4,use_clr=(10,20))
    name = 'ResNet50_512_59Max-{}-2'.format(fold_)
    learner.save(name)
    
    learner.fit(lrs/16,1,cycle_len=8,use_clr=(5,20))
    name = 'ResNet50_512_59Max-{}'.format(fold_)
    learner.save(name)
    
    preds,y = learner.TTA(n_aug=16)
    preds = np.stack(preds, axis=-1)
    preds = sigmoid_np(preds)
    pred = preds.max(axis=-1)
    
    preds_t,y_t = learner.TTA(n_aug=16,is_test=True)
    preds_t = np.stack(preds_t, axis=-1)
    preds_t = sigmoid_np(preds_t)
    pred_t = preds_t.max(axis=-1)
    
    sub_class_preds += pred_t
    for ii, idx in enumerate(valid_indexes):
        oof_class_preds[idx] = pred[ii]
    
    np.save('../cache/sub_class_preds-59', sub_class_preds)
    np.save('../cache/oof_class_preds-59', oof_class_preds)
    
    del learner
    import gc
    gc.collect()
    
    fold_ += 1

[     0      1      2 ... 105674 105675 105676] [     8     23     24 ... 105664 105670 105677]
[     0      2      3 ... 105675 105676 105677] [     1      6      7 ... 105650 105668 105673]
[     1      2      3 ... 105675 105676 105677] [     0      4     11 ... 105665 105666 105669]
[     0      1      2 ... 105673 105674 105677] [     3      9     10 ... 105671 105675 105676]
[     0      1      3 ... 105675 105676 105677] [     2      5     15 ... 105667 105672 105674]


HBox(children=(IntProgress(value=0, description='Epoch', max=1, style=ProgressStyle(description_width='initial')), HTML(value='')))

epoch      trn_loss   val_loss   acc                           
    0      1.039639   1.020645   0.955424  



HBox(children=(IntProgress(value=0, description='Epoch', max=8, style=ProgressStyle(description_width='initial')), HTML(value='')))

epoch      trn_loss   val_loss   acc                             
    0      0.770167   0.700482   0.969092  
    1      0.71237    0.651345   0.971059                        
    2      0.719186   0.660607   0.970687                        
    3      0.684846   0.625314   0.972258                        
    4      0.678509   0.643206   0.971346                        
    5      0.664521   0.612112   0.972679                        
    6      0.699329   0.627001   0.971995                        
    7      0.65341    0.602834   0.973149                        



HBox(children=(IntProgress(value=0, description='Epoch', max=8, style=ProgressStyle(description_width='initial')), HTML(value='')))

epoch      trn_loss   val_loss   acc                             
    0      0.695292   0.625302   0.972231  
    1      0.651356   0.613231   0.972608                        
    2      0.636593   0.597976   0.973247                        
    3      0.630159   0.591245   0.973656                        
    4      0.673091   0.617202   0.972461                        
    5      0.629386   0.602308   0.972995                        
    6      0.592347   0.589827   0.973598                        
    7      0.558129   0.580204   0.973987                        



HBox(children=(IntProgress(value=0, description='Epoch', max=8, style=ProgressStyle(description_width='initial')), HTML(value='')))

epoch      trn_loss   val_loss   acc                             
    0      0.597861   0.589752   0.973477  
    1      0.584773   0.584284   0.973776                        
    2      0.572528   0.585383   0.973884                        
    3      0.572714   0.582784   0.973995                        
    4      0.593582   0.58181    0.974                           
    5      0.557349   0.582522   0.973928                        
    6      0.548942   0.577302   0.974149                        
    7      0.546686   0.574196   0.974306                        



In [4]:
# import numpy as np
# my_train_indexes = list(np.load('../cache/train_indexes_60max.npy'))
# my_valid_indexes = list(np.load('../cache/valid_indexes_60max.npy'))

# for train_indexes, valid_indexes in zip(my_train_indexes, my_valid_indexes):
#     print(len(train_indexes), len(valid_indexes))
# 72010 36005
# 72010 36005
# 72010 36005

72010 36005
72010 36005
72010 36005


In [5]:
72010/16

4500.625

In [48]:
sub_class_preds = np.load('../cache/sub_class_preds-59.npy')

In [26]:
sub_class_preds /= 5

In [49]:
pred = oof_class_preds
pred_t = sub_class_preds

In [50]:
pred_t

array([[2.19351, 0.28715, 1.191  , ..., 2.02153, 0.50969, 0.24361],
       [1.30008, 0.34609, 1.40622, ..., 2.69136, 0.57136, 0.23937],
       [2.5458 , 1.29427, 1.90875, ..., 2.23322, 0.55188, 0.15393],
       ...,
       [2.15109, 0.39516, 0.73383, ..., 2.12602, 0.72538, 0.44066],
       [2.15383, 0.46413, 1.11342, ..., 1.70791, 0.28892, 0.13498],
       [2.88804, 1.20156, 1.48881, ..., 1.70794, 0.47116, 0.19528]])

In [47]:
pred_t

array([[0.4387 , 0.05743, 0.2382 , ..., 0.40431, 0.10194, 0.04872],
       [0.26002, 0.06922, 0.28124, ..., 0.53827, 0.11427, 0.04787],
       [0.50916, 0.25885, 0.38175, ..., 0.44664, 0.11038, 0.03079],
       ...,
       [0.43022, 0.07903, 0.14677, ..., 0.4252 , 0.14508, 0.08813],
       [0.43077, 0.09283, 0.22268, ..., 0.34158, 0.05778, 0.027  ],
       [0.57761, 0.24031, 0.29776, ..., 0.34159, 0.09423, 0.03906]])

In [30]:
pred.shape, pred_t.shape

((105678, 28), (11702, 28))

In [25]:
fold_ = 0
sub_class_preds = np.zeros((20, submit.shape[0], 28))
for train_indexes, valid_indexes in zip(my_train_indexes, my_valid_indexes):
#     if fold_ != 4:
#         fold_ += 1
#         print(train_indexes, valid_indexes)
#         continue
    print(train_indexes, valid_indexes)
    tr_n = [train_names[i] for i in train_indexes]
    val_n = [train_names[i] for i in valid_indexes]
    
    def get_data(sz,bs):
        #data augmentation
        aug_tfms = [RandomRotate(30, tfm_y=TfmType.NO),
                    RandomDihedral(tfm_y=TfmType.NO),
                    RandomLighting(0.05, 0.05, tfm_y=TfmType.NO)]
        #mean and std in of each channel in the train set
    #     stats = A([0.08069, 0.05258, 0.05487, 0.08282], [0.13704, 0.10145, 0.15313, 0.13814])
    #     stats = A([0.08069, 0.05258, 0.05487], [0.13704, 0.10145, 0.15313])
        stats = A([0.0751 , 0.05909, 0.04364], [0.11428, 0.09856, 0.09925])
        tfms = tfms_from_stats(stats, sz, crop_type=CropType.NO, tfm_y=TfmType.NO, 
                    aug_tfms=aug_tfms)
        ds = ImageData.get_ds(pdFilesDataset, (tr_n[:-(len(tr_n)%bs)],TRAIN), 
                    (val_n,TRAIN), tfms, test=(test_names,TEST))
        md = ImageData(PATH, ds, bs, num_workers=nw, classes=None)
        return md
    
    bs = 16
    sz = 512
    md = get_data(sz,bs)

    learner = ConvLearner.pretrained(arch, md, ps=0.5) #dropout 50%
    learner.opt_fn = optim.Adam
    learner.clip = 1.0 #gradient clipping
    learner.crit = FocalLoss()
    learner.metrics = [acc]
    
#     lr = 8e-4
#     learner.fit(lr,1)
#     name = 'ResNet50_512_59Max-{}-0'.format(fold_)
#     learner.save(name)
    
#     learner.unfreeze()
#     lrs=np.array([lr/10,lr/3,lr])
    
#     learner.fit(lrs/4,4,cycle_len=2,use_clr=(10,20))
#     name = 'ResNet50_512_59Max-{}-1'.format(fold_)
#     learner.save(name)
    
#     learner.fit(lrs/4,2,cycle_len=4,use_clr=(10,20))
#     name = 'ResNet50_512_59Max-{}-2'.format(fold_)
#     learner.save(name)
    
#     learner.fit(lrs/16,1,cycle_len=8,use_clr=(5,20))
    name = 'ResNet50_512_59Max-{}'.format(fold_)
    print(name)
#     learner.save(name)
    learner.load(name)
#     preds,y = learner.TTA(n_aug=16)
#     preds = np.stack(preds, axis=-1)
#     preds = sigmoid_np(preds)
#     pred = preds.max(axis=-1)
    
    preds_t,y_t = learner.TTA(n_aug=16,is_test=True)
#     preds_t = np.stack(preds_t, axis=-1)
#     preds_t = sigmoid_np(preds_t)
#     pred_t = preds_t.max(axis=-1)
    
    sub_class_preds += preds_t
    
    
#     del learner
#     import gc
#     gc.collect()
    
    fold_ += 1

[     0      1      2 ... 105674 105675 105676] [     8     23     24 ... 105664 105670 105677]
<function resnet50 at 0x7f10b3e09598>
Here-------1
Here-------11
ResNet50_512_59Max-0
[     0      2      3 ... 105675 105676 105677] [     1      6      7 ... 105650 105668 105673]
<function resnet50 at 0x7f10b3e09598>
Here-------1
Here-------11
ResNet50_512_59Max-1
[     1      2      3 ... 105675 105676 105677] [     0      4     11 ... 105665 105666 105669]
<function resnet50 at 0x7f10b3e09598>
Here-------1
Here-------11
ResNet50_512_59Max-2
[     0      1      2 ... 105673 105674 105677] [     3      9     10 ... 105671 105675 105676]
<function resnet50 at 0x7f10b3e09598>
Here-------1
Here-------11
ResNet50_512_59Max-3
[     0      1      3 ... 105675 105676 105677] [     2      5     15 ... 105667 105672 105674]
<function resnet50 at 0x7f10b3e09598>
Here-------1
Here-------11
ResNet50_512_59Max-4


In [26]:
sub_class_preds /= 5

In [27]:
np.save('../cache/sub_class_preds-59-1', sub_class_preds)

In [28]:
preds_t = sub_class_preds

In [29]:
preds_t = np.stack(preds_t, axis=-1)
preds_t = sigmoid_np(preds_t)
pred_t = preds_t.max(axis=-1)

In [30]:
def save_pred(pred, th=0.5, fname='../submissions/sub59-max.csv'):
    pred_list = []
    for line in pred:
        s = ' '.join(list([str(i) for i in np.nonzero(line>th)[0]]))
        pred_list.append(s)
        
    sample_df = pd.read_csv(SAMPLE)
    sample_list = list(sample_df.Id)
    pred_dic = dict((key, value) for (key, value) 
                in zip(test_names,pred_list))
    pred_list_cor = [pred_dic[id] for id in sample_list]
    df = pd.DataFrame({'Id':sample_list,'Predicted':pred_list_cor})
    df.to_csv(fname, header=True, index=False)

In [31]:
# pred_t = sub_class_preds

In [32]:
# pred_t /= 5

In [33]:
pred_t

array([[0.73493, 0.05055, 0.74015, ..., 0.52403, 0.03339, 0.00585],
       [0.73273, 0.01795, 0.22054, ..., 0.57766, 0.02326, 0.01873],
       [0.48371, 0.10199, 0.2098 , ..., 0.65127, 0.10585, 0.02547],
       ...,
       [0.48372, 0.09918, 0.23814, ..., 0.40385, 0.1171 , 0.07773],
       [0.78831, 0.05755, 0.15571, ..., 0.5778 , 0.05669, 0.01713],
       [0.15758, 0.06608, 0.83064, ..., 0.25081, 0.03028, 0.01899]])

In [61]:
pred_t

array([[0.146  , 0.07454, 0.13957, ..., 0.51027, 0.06531, 0.05267],
       [0.19795, 0.07618, 0.59151, ..., 0.37365, 0.05107, 0.02737],
       [0.29757, 0.04844, 0.43544, ..., 0.64897, 0.15358, 0.03462],
       ...,
       [0.31409, 0.03006, 0.13921, ..., 0.41325, 0.05142, 0.14242],
       [0.75039, 0.01483, 0.06946, ..., 0.73099, 0.02515, 0.00369],
       [0.62666, 0.90677, 0.22338, ..., 0.14869, 0.0215 , 0.00129]])

In [57]:
pred_t

array([[0.4387 , 0.05743, 0.2382 , ..., 0.40431, 0.10194, 0.04872],
       [0.26002, 0.06922, 0.28124, ..., 0.53827, 0.11427, 0.04787],
       [0.50916, 0.25885, 0.38175, ..., 0.44664, 0.11038, 0.03079],
       ...,
       [0.43022, 0.07903, 0.14677, ..., 0.4252 , 0.14508, 0.08813],
       [0.43077, 0.09283, 0.22268, ..., 0.34158, 0.05778, 0.027  ],
       [0.57761, 0.24031, 0.29776, ..., 0.34159, 0.09423, 0.03906]])

In [34]:
th_t = np.array([0.565,0.39,0.55,0.345,0.33,0.39,0.33,0.45,0.38,0.39,
               0.34,0.42,0.31,0.38,0.49,0.50,0.38,0.43,0.46,0.40,
               0.39,0.505,0.37,0.47,0.41,0.545,0.32,0.1])
print('Fractions: ',(pred_t > th_t).mean(axis=0))
save_pred(pred_t,th_t)

Fractions:  [0.37737 0.04127 0.07529 0.04982 0.0582  0.08272 0.04734 0.07469 0.00068 0.00068 0.00077 0.03965 0.03358
 0.01769 0.04239 0.      0.03324 0.02282 0.02974 0.05341 0.00624 0.13374 0.02948 0.0811  0.01179 0.25303
 0.02555 0.02854]


In [35]:
lb_prob = [
 0.362397820,0.043841336,0.075268817,0.059322034,0.075268817,
 0.075268817,0.043841336,0.075268817,0.010000000,0.010000000,
 0.010000000,0.043841336,0.043841336,0.014198783,0.043841336,
 0.010000000,0.028806584,0.014198783,0.028806584,0.059322034,
 0.010000000,0.126126126,0.028806584,0.075268817,0.010000000,
 0.222493880,0.028806584,0.010000000]

In [36]:
def Count_soft(preds,th=0.5,d=50.0):
    preds = sigmoid_np(d*(preds - th))
    return preds.mean(axis=0)

def fit_test(x,y):
    params = 0.5*np.ones(len(name_label_dict))
    wd = 1e-5
    error = lambda p: np.concatenate((Count_soft(x,p) - y,
                                      wd*(p - 0.5)), axis=None)
    p, success = opt.leastsq(error, params)
    return p

In [37]:
th_t = fit_test(pred_t,lb_prob)
th_t[th_t<0.1] = 0.1
print('Thresholds: ',th_t)
print('Fractions: ',(pred_t > th_t).mean(axis=0))
print('Fractions (th = 0.5): ',(pred_t > 0.5).mean(axis=0))

Thresholds:  [0.57906 0.36776 0.55362 0.31088 0.2868  0.41401 0.34664 0.45035 0.1255  0.13552 0.13088 0.39319 0.27113
 0.47199 0.47351 0.13717 0.41219 0.56242 0.46865 0.38101 0.30697 0.51917 0.38156 0.49536 0.49236 0.56891
 0.30743 0.16018]
Fractions:  [0.36319 0.04341 0.07477 0.057   0.07187 0.07366 0.04179 0.07469 0.00453 0.00607 0.00538 0.04273 0.04076
 0.01401 0.04358 0.00461 0.02786 0.01427 0.0282  0.0582  0.00957 0.12528 0.02769 0.07512 0.00991 0.2203
 0.0282  0.00496]
Fractions (th = 0.5):  [0.43728 0.03538 0.0852  0.03256 0.03546 0.05221 0.01795 0.06332 0.00051 0.00051 0.00026 0.03367 0.01923
 0.01316 0.04204 0.      0.01914 0.01735 0.0229  0.03239 0.00342 0.13716 0.01735 0.07418 0.00983 0.31644
 0.01034 0.00009]


In [38]:
save_pred(pred_t,th_t,'../submissions/sub59-max-f-1.csv')

In [39]:
# save_pred(pred_t,th,'../submissions/sub59-max-v.csv')
save_pred(pred_t,0.5,'../submissions/sub59-max-05-1.csv')

In [40]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub59-max-05-1.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 467k/467k [00:12<00:00, 39.2kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName             date                 description  status    publicScore  privateScore  
-------------------  -------------------  -----------  --------  -----------  ------------  
sub59-max-05-1.csv   2019-01-01 08:59:47               complete  0.500        None          
sub50-max-045-l.csv  2019-01-01 05:15:38               complete  0.569        None          
sub59-max-040.csv    2019-01-01 05:12:22               complete  0.530        None          
sub59-max-045.csv    2018-12-31 08:45:31               complete  0.545        None          
sub59-max-049.csv    2018-12-31 08:44:03               complete  0.535        None          
sub59-max-051.csv    2018-12-31 08:43:00               complete  0.525        None          
sub59-max-05.csv     2018-12-31 08:41:36               complete  0.530        None          
sub59-max-05.csv

In [41]:
# save_pred(pred_t,0.5,'../submissions/sub50-max-05.csv')
save_pred(pred_t,0.45,'../submissions/sub59-max-045-1.csv')
save_pred(pred_t,0.55,'../submissions/sub59-max-055-1.csv')
# save_pred(pred_t,0.35,'../submissions/sub59-max-035.csv')
# save_pred(pred_t,0.30,'../submissions/sub59-max-030.csv')
# save_pred(pred_t,0.25,'../submissions/sub59-max-025.csv')

In [42]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub59-max-045-1.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 475k/475k [00:12<00:00, 39.8kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName             date                 description  status    publicScore  privateScore  
-------------------  -------------------  -----------  --------  -----------  ------------  
sub59-max-045-1.csv  2019-01-01 09:01:41               complete  0.520        None          
sub59-max-05-1.csv   2019-01-01 08:59:47               complete  0.500        None          
sub50-max-045-l.csv  2019-01-01 05:15:38               complete  0.569        None          
sub59-max-040.csv    2019-01-01 05:12:22               complete  0.530        None          
sub59-max-045.csv    2018-12-31 08:45:31               complete  0.545        None          
sub59-max-049.csv    2018-12-31 08:44:03               complete  0.535        None          
sub59-max-051.csv    2018-12-31 08:43:00               complete  0.525        None          
sub59-max-05.csv

In [70]:
save_pred(pred_t,0.45,'../submissions/sub59-max-045.csv')

In [73]:
save_pred(pred_t,0.40,'../submissions/sub59-max-040.csv')
save_pred(pred_t,0.35,'../submissions/sub59-max-035.csv')
save_pred(pred_t,0.30,'../submissions/sub59-max-030.csv')
save_pred(pred_t,0.25,'../submissions/sub59-max-025.csv')

In [40]:
class_list = [8,9,10,15,20,24,27]
for i in class_list:
    th_t[i] = th[i]
save_pred(pred_t,th_t,'../submissions/sub59-max-c.csv')

NameError: name 'th' is not defined

In [43]:
labels = pd.read_csv(LABELS).set_index('Id')
label_count = np.zeros(len(name_label_dict))
for label in labels['Target']:
    l = [int(i) for i in label.split()]
    label_count += np.eye(len(name_label_dict))[l].sum(axis=0)
label_fraction = label_count.astype(np.float)/len(labels)
label_count, label_fraction

(array([40958.,  3072., 10871.,  3329.,  5130.,  5938.,  3725.,  9405.,   217.,   197.,   182.,  2194.,
         2233.,  1458.,  2692.,    63.,  1290.,   446.,  1893.,  3672.,   438., 13809.,  2729., 10345.,
          428., 37366.,   706.,   127.]),
 array([0.38757, 0.02907, 0.10287, 0.0315 , 0.04854, 0.05619, 0.03525, 0.089  , 0.00205, 0.00186, 0.00172,
        0.02076, 0.02113, 0.0138 , 0.02547, 0.0006 , 0.01221, 0.00422, 0.01791, 0.03475, 0.00414, 0.13067,
        0.02582, 0.09789, 0.00405, 0.35358, 0.00668, 0.0012 ]))

In [44]:
th_t = fit_test(pred_t,label_fraction)
th_t[th_t<0.05] = 0.05
print('Thresholds: ',th_t)
print('Fractions: ',(pred_t > th_t).mean(axis=0))
save_pred(pred_t,th_t,'../submissions/sub50-max-t.csv')

Thresholds:  [0.61031 0.69905 0.46599 0.605   0.46466 0.55995 0.45961 0.50596 0.28119 0.32072 0.30641 0.76949 0.50039
 0.5588  0.77093 0.28936 0.79564 0.93314 0.60171 0.57444 0.62792 0.54489 0.4801  0.52909 0.8591  0.4939
 0.66123 0.28138]
Fractions:  [0.38908 0.02931 0.10195 0.03145 0.04794 0.0564  0.03401 0.08793 0.00197 0.00162 0.00171 0.02119 0.02094
 0.01367 0.02555 0.0006  0.01222 0.00419 0.01743 0.03427 0.00436 0.12938 0.02504 0.09674 0.00419 0.35267
 0.00641 0.00085]


In [66]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub59-max-05.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 476k/476k [00:12<00:00, 39.4kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName             date                 description  status    publicScore  privateScore  
-------------------  -------------------  -----------  --------  -----------  ------------  
sub59-max-05.csv     2018-12-31 08:41:36               complete  0.530        None          
sub59-max-05.csv     2018-12-31 04:33:36               complete  0.045        None          
sub50-mag-05.csv     2018-12-29 06:10:25               complete  0.445        None          
sub_43max_test5.csv  2018-12-24 15:30:31               complete  0.568        None          
sub_43max_test4.csv  2018-12-24 15:27:46               complete  0.475        None          
sub_43max_test3.csv  2018-12-24 15:22:17               complete  0.101        None          
sub_43max_test2.csv  2018-12-24 15:18:02               complete  0.088        None          
sub_43max_test1.

In [68]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub59-max-051.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 474k/474k [00:12<00:00, 39.4kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName             date                 description  status    publicScore  privateScore  
-------------------  -------------------  -----------  --------  -----------  ------------  
sub59-max-051.csv    2018-12-31 08:43:00               complete  0.525        None          
sub59-max-05.csv     2018-12-31 08:41:36               complete  0.530        None          
sub59-max-05.csv     2018-12-31 04:33:36               complete  0.045        None          
sub50-mag-05.csv     2018-12-29 06:10:25               complete  0.445        None          
sub_43max_test5.csv  2018-12-24 15:30:31               complete  0.568        None          
sub_43max_test4.csv  2018-12-24 15:27:46               complete  0.475        None          
sub_43max_test3.csv  2018-12-24 15:22:17               complete  0.101        None          
sub_43max_test2.

In [69]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub59-max-049.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 477k/477k [00:13<00:00, 37.4kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName             date                 description  status    publicScore  privateScore  
-------------------  -------------------  -----------  --------  -----------  ------------  
sub59-max-049.csv    2018-12-31 08:44:03               complete  0.535        None          
sub59-max-051.csv    2018-12-31 08:43:00               complete  0.525        None          
sub59-max-05.csv     2018-12-31 08:41:36               complete  0.530        None          
sub59-max-05.csv     2018-12-31 04:33:36               complete  0.045        None          
sub50-mag-05.csv     2018-12-29 06:10:25               complete  0.445        None          
sub_43max_test5.csv  2018-12-24 15:30:31               complete  0.568        None          
sub_43max_test4.csv  2018-12-24 15:27:46               complete  0.475        None          
sub_43max_test3.

In [71]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub59-max-045.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 486k/486k [00:15<00:00, 32.1kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName             date                 description  status    publicScore  privateScore  
-------------------  -------------------  -----------  --------  -----------  ------------  
sub59-max-045.csv    2018-12-31 08:45:31               complete  0.545        None          
sub59-max-049.csv    2018-12-31 08:44:03               complete  0.535        None          
sub59-max-051.csv    2018-12-31 08:43:00               complete  0.525        None          
sub59-max-05.csv     2018-12-31 08:41:36               complete  0.530        None          
sub59-max-05.csv     2018-12-31 04:33:36               complete  0.045        None          
sub50-mag-05.csv     2018-12-29 06:10:25               complete  0.445        None          
sub_43max_test5.csv  2018-12-24 15:30:31               complete  0.568        None          
sub_43max_test4.

In [1]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub59-max-040.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 498k/498k [00:19<00:00, 25.8kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName             date                 description  status    publicScore  privateScore  
-------------------  -------------------  -----------  --------  -----------  ------------  
sub59-max-040.csv    2019-01-01 05:12:22               complete  0.530        None          
sub59-max-045.csv    2018-12-31 08:45:31               complete  0.545        None          
sub59-max-049.csv    2018-12-31 08:44:03               complete  0.535        None          
sub59-max-051.csv    2018-12-31 08:43:00               complete  0.525        None          
sub59-max-05.csv     2018-12-31 08:41:36               complete  0.530        None          
sub59-max-05.csv     2018-12-31 04:33:36               complete  0.045        None          
sub50-mag-05.csv     2018-12-29 06:10:25               complete  0.445        None          
sub_43max_test5.

In [3]:
import pandas as pd

In [4]:
leak_test = pd.read_csv('../cache/leak_test.csv')
sub50 = pd.read_csv('../submissions/sub50-max-045.csv')
for idx, row in leak_test.iterrows():
    test_id = row['Id']
    target = row['Target']
    sub50.loc[sub50.Id == test_id, 'Predicted'] = target

In [5]:
sub50.to_csv('../submissions/sub50-max-045-l.csv', index=False)

In [6]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub50-max-045-l.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 486k/486k [00:12<00:00, 39.3kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName             date                 description  status    publicScore  privateScore  
-------------------  -------------------  -----------  --------  -----------  ------------  
sub50-max-045-l.csv  2019-01-01 05:15:38               complete  0.569        None          
sub59-max-040.csv    2019-01-01 05:12:22               complete  0.530        None          
sub59-max-045.csv    2018-12-31 08:45:31               complete  0.545        None          
sub59-max-049.csv    2018-12-31 08:44:03               complete  0.535        None          
sub59-max-051.csv    2018-12-31 08:43:00               complete  0.525        None          
sub59-max-05.csv     2018-12-31 08:41:36               complete  0.530        None          
sub59-max-05.csv     2018-12-31 04:33:36               complete  0.045        None          
sub50-mag-05.csv

In [49]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub50-max-c.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 468k/468k [00:08<00:00, 49.1kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName           date                 description  status    publicScore  privateScore  
-----------------  -------------------  -----------  --------  -----------  ------------  
sub50-max-c.csv    2018-12-14 04:52:04               complete  0.523        None          
sub50-max-t-l.csv  2018-12-14 04:48:42               complete  0.533        None          
sub50-max-t.csv    2018-12-14 02:56:13               complete  0.507        None          
sub48-max-b.csv    2018-12-12 06:57:44               complete  0.449        None          
sub48-max-a.csv    2018-12-12 06:55:45               complete  0.457        None          
sub44-max-t.csv    2018-12-10 20:51:55               complete  0.019        None          
sub41-t-l.csv      2018-12-08 09:27:37               complete  0.541        None          
sub41-max-b.csv    2018-12-08 08:0

In [53]:
leak_test = pd.read_csv('../cache/leak_test.csv')
sub50 = pd.read_csv('../submissions/sub50-max-c.csv')
for idx, row in leak_test.iterrows():
    test_id = row['Id']
    target = row['Target']
    sub50.loc[sub50.Id == test_id, 'Predicted'] = target
sub50.to_csv('../submissions/sub50-max-c-l.csv', index=False)

In [54]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub50-max-c-l.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

fileName           date                 description  status    publicScore  privateScore  
-----------------  -------------------  -----------  --------  -----------  ------------  
sub50-max-c-l.csv  2018-12-14 04:52:55               complete  0.557        None          
sub50-max-c.csv    2018-12-14 04:52:04               complete  0.523        None          
sub50-max-t-l.csv  2018-12-14 04:48:42               complete  0.533        None          
sub50-max-t.csv    2018-12-14 02:56:13               complete  0.507        None          
sub48-max-b.csv    2018-12-12 06:57:44               complete  0.449        None          
sub48-max-a.csv    2018-12-12 06:55:45               complete  0.457        None          
sub44-max-t.csv    2018-12-10 20:51:55               complete  0.019        None          
sub41-t-l.csv      2018-12-08 09:27:37               complete  0.541        None          
sub41-max-b.csv    2018-12-08 08:04:32               complete  0.478        None          

In [55]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub50-max-05.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 476k/476k [00:13<00:00, 37.1kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName           date                 description  status    publicScore  privateScore  
-----------------  -------------------  -----------  --------  -----------  ------------  
sub50-max-05.csv   2018-12-14 04:56:42               complete  0.533        None          
sub50-max-c-l.csv  2018-12-14 04:52:55               complete  0.557        None          
sub50-max-c.csv    2018-12-14 04:52:04               complete  0.523        None          
sub50-max-t-l.csv  2018-12-14 04:48:42               complete  0.533        None          
sub50-max-t.csv    2018-12-14 02:56:13               complete  0.507        None          
sub48-max-b.csv    2018-12-12 06:57:44               complete  0.449        None          
sub48-max-a.csv    2018-12-12 06:55:45               complete  0.457        None          
sub44-max-t.csv    2018-12-10 20:5

In [6]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub50-max-045.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

fileName           date                 description  status    publicScore  privateScore  
-----------------  -------------------  -----------  --------  -----------  ------------  
sub50-max-045.csv  2018-12-15 05:36:27               complete  0.528        None          
sub50-max-05.csv   2018-12-14 04:56:42               complete  0.533        None          
sub50-max-c-l.csv  2018-12-14 04:52:55               complete  0.557        None          
sub50-max-c.csv    2018-12-14 04:52:04               complete  0.523        None          
sub50-max-t-l.csv  2018-12-14 04:48:42               complete  0.533        None          
sub50-max-t.csv    2018-12-14 02:56:13               complete  0.507        None          
sub48-max-b.csv    2018-12-12 06:57:44               complete  0.449        None          
sub48-max-a.csv    2018-12-12 06:55:45               complete  0.457        None          
sub44-max-t.csv    2018-12-10 20:51:55               complete  0.019        None          

In [7]:
leak_test = pd.read_csv('../cache/leak_test.csv')
sub50 = pd.read_csv('../submissions/sub50-max-05.csv')
for idx, row in leak_test.iterrows():
    test_id = row['Id']
    target = row['Target']
    sub50.loc[sub50.Id == test_id, 'Predicted'] = target
sub50.to_csv('../submissions/sub50-max-05-l.csv', index=False)

In [9]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub50-max-05-l.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 476k/476k [00:44<00:00, 10.8kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName            date                 description  status    publicScore  privateScore  
------------------  -------------------  -----------  --------  -----------  ------------  
sub50-max-05-l.csv  2018-12-15 05:44:54               complete  0.578        None          
sub50-max-045.csv   2018-12-15 05:36:27               complete  0.528        None          
sub50-max-05.csv    2018-12-14 04:56:42               complete  0.533        None          
sub50-max-c-l.csv   2018-12-14 04:52:55               complete  0.557        None          
sub50-max-c.csv     2018-12-14 04:52:04               complete  0.523        None          
sub50-max-t-l.csv   2018-12-14 04:48:42               complete  0.533        None          
sub50-max-t.csv     2018-12-14 02:56:13               complete  0.507        None          
sub48-max-b.csv     2018-

In [75]:
def save_pred(pred, th=0.5, fname='../submissions/sub50-max-notta.csv'):
    pred_list = []
    for line in pred:
        s = ' '.join(list([str(i) for i in np.nonzero(line>th)[0]]))
        pred_list.append(s)
        
    sample_df = pd.read_csv(SAMPLE)
    sample_list = list(sample_df.Id)
    pred_dic = dict((key, value) for (key, value) 
                in zip(learner.data.test_ds.fnames,pred_list))
    pred_list_cor = [pred_dic[id] for id in sample_list]
    df = pd.DataFrame({'Id':sample_list,'Predicted':pred_list_cor})
    df.to_csv(fname, header=True, index=False)

In [76]:
th_t = np.array([0.565,0.39,0.55,0.345,0.33,0.39,0.33,0.45,0.38,0.39,
               0.34,0.42,0.31,0.38,0.49,0.50,0.38,0.43,0.46,0.40,
               0.39,0.505,0.37,0.47,0.41,0.545,0.32,0.1])
print('Fractions: ',(pred_t > th_t).mean(axis=0))
save_pred(pred_t,th_t)

ValueError: operands could not be broadcast together with shapes (11702,) (28,) 

In [60]:
# pred= preds_t
# fname='../submissions/sub50-max-notta.csv'
# th=0.5
# pred_list = []
# for line in pred:
#     s = ' '.join(list([str(i) for i in np.nonzero(line>th)[0]]))
#     pred_list.append(s)
# sample_df = pd.read_csv(SAMPLE)
# sample_list = list(sample_df.Id)
# pred_dic = dict((key, value) for (key, value) 
#             in zip(learner.data.test_ds.fnames,pred_list))
# pred_list_cor = [pred_dic[id] for id in sample_list]
# df = pd.DataFrame({'Id':sample_list,'Predicted':pred_list_cor})
# df.to_csv(fname, header=True, index=False)

In [61]:
df.shape

(11702, 2)

In [62]:
df.head()

Id Predicted
0  00008af0-bad0-11e8-b2b8-ac1f6b6435d0         2
1  0000a892-bacf-11e8-b2b8-ac1f6b6435d0         5
2  0006faa6-bac7-11e8-b2b7-ac1f6b6435d0    0 5 25
3  0008baca-bad7-11e8-b2b9-ac1f6b6435d0         0
4  000cce7e-bad4-11e8-b2b8-ac1f6b6435d0        23

In [80]:
save_pred(pred_t,0.5,'../submissions/sub50-max-05-notta.csv')

In [84]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub50-max-05-notta.csv -m ""
from time import sleep
sleep(10)
!kaggle competitions submissions -c human-protein-atlas-image-classification

fileName                date                 description  status    publicScore  privateScore  
----------------------  -------------------  -----------  --------  -----------  ------------  
sub50-max-05-notta.csv  2018-12-15 08:41:36               complete  0.020        None          
sub50-max-05-notta.csv  2018-12-15 08:22:48               complete  0.020        None          
sub54-max-a.csv         2018-12-15 06:06:02               complete  0.365        None          
sub50-max-05-l.csv      2018-12-15 05:44:54               complete  0.578        None          
sub50-max-045.csv       2018-12-15 05:36:27               complete  0.528        None          
sub50-max-05.csv        2018-12-14 04:56:42               complete  0.533        None          
sub50-max-c-l.csv       2018-12-14 04:52:55               complete  0.557        None          
sub50-max-c.csv         2018-12-14 04:52:04               complete  0.523        None          
sub50-max-t-l.csv       2018-12-14 04:48

In [9]:
%%time
!kaggle competitions submit -c human-protein-atlas-image-classification -f ../submissions/sub50_22.csv -m ""
from time import sleep
sleep(30)
!kaggle competitions submissions -c human-protein-atlas-image-classification

100%|████████████████████████████████████████| 476k/476k [00:12<00:00, 37.6kB/s]
Successfully submitted to Human Protein Atlas Image ClassificationfileName                date                 description  status    publicScore  privateScore  
----------------------  -------------------  -----------  --------  -----------  ------------  
sub50_22.csv            2018-12-16 02:56:59               complete  0.579        None          
sub50_22.csv            2018-12-16 02:32:16               complete  0.578        None          
sub50_22.csv            2018-12-16 02:16:49               complete  0.059        None          
sub50_22.csv            2018-12-16 02:00:57               complete  0.059        None          
sub50-max-05-notta.csv  2018-12-15 08:41:36               complete  0.020        None          
sub50-max-05-notta.csv  2018-12-15 08:22:48               complete  0.020        None          
sub54-max-a.csv         2018-12-15 06:06:02               complete  0.365        None

In [11]:
# !pip install imagehash

In [13]:
import pickle
import numpy as np
from imagehash import phash
from math import sqrt

def match(h1,h2, h2ps, color):
    for p1 in h2ps[h1]:
        for p2 in h2ps[h2]:
            i1 =  pil_image.open(expand_path(p1) + '_' + color + '.png')
            i2 =  pil_image.open(expand_path(p2) + '_' + color + '.png')
#             if i1.mode != i2.mode or i1.size != i2.size: return False
            a1 = np.array(i1)
            a1 = a1 - a1.mean()
            a1 = a1/sqrt((a1**2).mean())
            a2 = np.array(i2)
            a2 = a2 - a2.mean()
            a2 = a2/sqrt((a2**2).mean())
            a  = ((a1 - a2)**2).mean()
#             if a > 0.1: return False
#             if a > 1.0: return False
            return a
    return 0.0
#     return True

In [12]:
tagged = dict([(p,w) for _,p,w in pd.read_csv('../data/train_combined_all.csv').to_records()])
submit = [p for _,p,_ in pd.read_csv('../data/sample_submission.csv').to_records()]
join   = list(tagged.keys()) + submit
len(tagged),len(submit),len(join),list(tagged.items())[:5],submit[:5]


(105678,
 11702,
 117380,
 [('00070df0-bbc3-11e8-b2bc-ac1f6b6435d0', '16 0'),
  ('000a6c98-bb9b-11e8-b2b9-ac1f6b6435d0', '7 1 2 0'),
  ('000a9596-bbc4-11e8-b2bc-ac1f6b6435d0', '5'),
  ('000c99ba-bba4-11e8-b2b9-ac1f6b6435d0', '1'),
  ('001838f8-bbca-11e8-b2bc-ac1f6b6435d0', '18')],
 ['00008af0-bad0-11e8-b2b8-ac1f6b6435d0',
  '0000a892-bacf-11e8-b2b8-ac1f6b6435d0',
  '0006faa6-bac7-11e8-b2b7-ac1f6b6435d0',
  '0008baca-bad7-11e8-b2b9-ac1f6b6435d0',
  '000cce7e-bad4-11e8-b2b8-ac1f6b6435d0'])

In [13]:
from os.path import isfile
from PIL import Image as pil_image
from tqdm import tqdm_notebook

In [14]:
def expand_path(p):
    if isfile('../data/train_combined/' + p + '_green.png'): return '../data/train_combined/' + p
    if isfile('../data/test/' + p + '_green.png'): return '../data/test/' + p
    return p

In [35]:
p2h_red = {}
p2h_green = {}
p2h_blue = {}
for p in tqdm_notebook(join):
    img1    = pil_image.open(expand_path(p) + '_red.png')
    img2    = pil_image.open(expand_path(p) + '_green.png')
    img3    = pil_image.open(expand_path(p) + '_blue.png')
    
    h1      = phash(img1)
    p2h_red[p] = h1

    h2      = phash(img2)
    p2h_green[p] = h2
    
    h3      = phash(img3)
    p2h_blue[p] = h3

HBox(children=(IntProgress(value=0, max=117380), HTML(value='')))

KeyboardInterrupt: 

In [36]:
p2h_red

{'00070df0-bbc3-11e8-b2bc-ac1f6b6435d0': array([[ True,  True,  True,  True, False, False, False,  True],
        [False, False, False, False, False,  True,  True,  True],
        [ True,  True, False,  True,  True,  True, False,  True],
        [False, False,  True,  True,  True,  True,  True, False],
        [False, False, False,  True, False,  True,  True, False],
        [False,  True, False,  True, False, False, False, False],
        [False, False, False,  True, False,  True,  True,  True],
        [False,  True,  True,  True,  True, False, False, False]]),
 '000a6c98-bb9b-11e8-b2b9-ac1f6b6435d0': array([[ True,  True,  True,  True, False,  True,  True, False],
        [ True,  True, False, False,  True,  True,  True,  True],
        [False, False, False, False, False, False, False, False],
        [False,  True, False, False,  True,  True,  True, False],
        [False, False,  True, False,  True, False,  True,  True],
        [ True, False, False,  True,  True, False, False,  T

In [13]:
# with open('../cache/p2h_red.pkl', 'rb') as f:
#     p2h_red = pickle.load(f)
# with open('../cache/p2h_green.pkl', 'rb') as f:
#     p2h_green = pickle.load(f)
# with open('../cache/p2h_blue.pkl', 'rb') as f:
#     p2h_blue = pickle.load(f)

In [42]:
# Find all images associated with a given phash value.
h2ps_red = {}
for p,h in tqdm_notebook(p2h_red.items()):
    if h not in h2ps_red: h2ps_red[h] = []
    if p not in h2ps_red[h]: h2ps_red[h].append(p)

# Find all distinct phash values
hs_red = list(h2ps_red.keys())

HBox(children=(IntProgress(value=0, max=117380), HTML(value='')))

In [15]:
h2ps_green = {}
for p,h in tqdm_notebook(p2h_green.items()):
    if h not in h2ps_green: h2ps_green[h] = []
    if p not in h2ps_green[h]: h2ps_green[h].append(p)

# Find all distinct phash values
hs_green = list(h2ps_green.keys())

HBox(children=(IntProgress(value=0, max=117380), HTML(value='')))

In [16]:
h2ps_blue= {}
for p,h in tqdm_notebook(p2h_blue.items()):
    if h not in h2ps_blue: h2ps_blue[h] = []
    if p not in h2ps_blue[h]: h2ps_blue[h].append(p)

# Find all distinct phash values
hs_blue = list(h2ps_blue.keys())

HBox(children=(IntProgress(value=0, max=117380), HTML(value='')))

In [15]:
# If the images are close enough, associate the two phash values (this is the slow part: n^2 algorithm)
h2h_red = {}
for i,h1 in enumerate(tqdm_notebook(hs_red)):
    for h2 in hs_red[:i]:
        if h1-h2 <= 10 and match(h1, h2, h2ps_red, 'red'):
            s1 = str(h1)
            s2 = str(h2)
            if s1 < s2: s1,s2 = s2,s1
            h2h_red[s1] = s2

HBox(children=(IntProgress(value=0, max=113281), HTML(value='')))

In [18]:
# If the images are close enough, associate the two phash values (this is the slow part: n^2 algorithm)
h2h_green = {}
for i,h1 in enumerate(tqdm_notebook(hs_green)):
    for h2 in hs_green[:i]:
        if h1-h2 <= 10 and match(h1, h2, h2ps_green, 'green'):
            s1 = str(h1)
            s2 = str(h2)
            if s1 < s2: s1,s2 = s2,s1
            h2h_green[s1] = s2

HBox(children=(IntProgress(value=0, max=113063), HTML(value='')))

In [19]:
# If the images are close enough, associate the two phash values (this is the slow part: n^2 algorithm)
h2h_blue = {}
for i,h1 in enumerate(tqdm_notebook(hs_blue)):
    for h2 in hs_blue[:i]:
        if h1-h2 <= 10 and match(h1, h2, h2ps_blue, 'blue'):
            s1 = str(h1)
            s2 = str(h2)
            if s1 < s2: s1,s2 = s2,s1
            h2h_blue[s1] = s2

HBox(children=(IntProgress(value=0, max=112571), HTML(value='')))

In [16]:
# Group together images with equivalent phash, and replace by string format of phash (faster and more readable)
for p,h in tqdm_notebook(p2h_red.items()):
    h = str(h)
    if h in h2h_red: h = h2h_red[h]
    p2h_red[p] = h

len(p2h_red), list(p2h_red.items())[:5]

HBox(children=(IntProgress(value=0, max=117380), HTML(value='')))

(117380,
 [('00070df0-bbc3-11e8-b2bc-ac1f6b6435d0', 'f107dd3e16501778'),
  ('000a6c98-bb9b-11e8-b2b9-ac1f6b6435d0', 'f6cf004e2b994c97'),
  ('000a9596-bbc4-11e8-b2bc-ac1f6b6435d0', 'c19e1f4a37646c74'),
  ('000c99ba-bba4-11e8-b2b9-ac1f6b6435d0', '898f179c7a8a5a99'),
  ('001838f8-bbca-11e8-b2bc-ac1f6b6435d0', '819734c19b919bb7')])

In [21]:
# Group together images with equivalent phash, and replace by string format of phash (faster and more readable)
for p,h in tqdm_notebook(p2h_green.items()):
    h = str(h)
    if h in h2h_green: h = h2h_green[h]
    p2h_green[p] = h

len(p2h_green), list(p2h_green.items())[:5]

HBox(children=(IntProgress(value=0, max=117380), HTML(value='')))

(117380,
 [('00070df0-bbc3-11e8-b2bc-ac1f6b6435d0', '847143d3d69cf686'),
  ('000a6c98-bb9b-11e8-b2b9-ac1f6b6435d0', 'd0ce054a6f991d9b'),
  ('000a9596-bbc4-11e8-b2bc-ac1f6b6435d0', 'c1cc5c4bb760743b'),
  ('000c99ba-bba4-11e8-b2b9-ac1f6b6435d0', '918f11987e6bea34'),
  ('001838f8-bbca-11e8-b2bc-ac1f6b6435d0', '85a1822abc7f975c')])

In [22]:
# Group together images with equivalent phash, and replace by string format of phash (faster and more readable)
for p,h in tqdm_notebook(p2h_blue.items()):
    h = str(h)
    if h in h2h_blue: h = h2h_blue[h]
    p2h_blue[p] = h

len(p2h_blue), list(p2h_blue.items())[:5]

HBox(children=(IntProgress(value=0, max=117380), HTML(value='')))

(117380,
 [('00070df0-bbc3-11e8-b2bc-ac1f6b6435d0', '8c7127d3d28cd12f'),
  ('000a6c98-bb9b-11e8-b2b9-ac1f6b6435d0', 'd04e054aefb94d93'),
  ('000a9596-bbc4-11e8-b2bc-ac1f6b6435d0', 'c0dc5ccb97707433'),
  ('000c99ba-bba4-11e8-b2b9-ac1f6b6435d0', 'd10fe1897e5f6814'),
  ('001838f8-bbca-11e8-b2bc-ac1f6b6435d0', '8d35222a8d57f74c')])

In [17]:
# For each image id, determine the list of pictures
h2ps_red = {}
for p,h in tqdm_notebook(p2h_red.items()):
    if h not in h2ps_red: h2ps_red[h] = []
    if p not in h2ps_red[h]: h2ps_red[h].append(p)

len(h2ps_red),list(h2ps_red.items())[:5]

HBox(children=(IntProgress(value=0, max=117380), HTML(value='')))

(112818,
 [('f107dd3e16501778', ['00070df0-bbc3-11e8-b2bc-ac1f6b6435d0']),
  ('f6cf004e2b994c97', ['000a6c98-bb9b-11e8-b2b9-ac1f6b6435d0']),
  ('c19e1f4a37646c74', ['000a9596-bbc4-11e8-b2bc-ac1f6b6435d0']),
  ('898f179c7a8a5a99', ['000c99ba-bba4-11e8-b2b9-ac1f6b6435d0']),
  ('819734c19b919bb7',
   ['001838f8-bbca-11e8-b2bc-ac1f6b6435d0', '64019_1169_H10_1'])])

In [40]:
import pickle
with open('../cache/p2h_red.pkl', 'wb') as f:
    pickle.dump(p2h_red, f)
with open('../cache/h2ps_red.pkl', 'wb') as f:
    pickle.dump(h2ps_red, f)

In [24]:
# For each image id, determine the list of pictures
h2ps_green = {}
for p,h in tqdm_notebook(p2h_green.items()):
    if h not in h2ps_green: h2ps_green[h] = []
    if p not in h2ps_green[h]: h2ps_green[h].append(p)

len(h2ps_green),list(h2ps_green.items())[:5]

HBox(children=(IntProgress(value=0, max=117380), HTML(value='')))

(113051,
 [('847143d3d69cf686', ['00070df0-bbc3-11e8-b2bc-ac1f6b6435d0']),
  ('d0ce054a6f991d9b', ['000a6c98-bb9b-11e8-b2b9-ac1f6b6435d0']),
  ('c1cc5c4bb760743b', ['000a9596-bbc4-11e8-b2bc-ac1f6b6435d0']),
  ('918f11987e6bea34', ['000c99ba-bba4-11e8-b2b9-ac1f6b6435d0']),
  ('85a1822abc7f975c', ['001838f8-bbca-11e8-b2bc-ac1f6b6435d0'])])

In [42]:
with open('../cache/p2h_green.pkl', 'wb') as f:
    pickle.dump(p2h_green, f)
with open('../cache/h2ps_green.pkl', 'wb') as f:
    pickle.dump(h2ps_green, f)

In [25]:
# For each image id, determine the list of pictures
h2ps_blue = {}
for p,h in tqdm_notebook(p2h_blue.items()):
    if h not in h2ps_blue: h2ps_blue[h] = []
    if p not in h2ps_blue[h]: h2ps_blue[h].append(p)

len(h2ps_blue),list(h2ps_blue.items())[:5]

HBox(children=(IntProgress(value=0, max=117380), HTML(value='')))

(112455,
 [('8c7127d3d28cd12f', ['00070df0-bbc3-11e8-b2bc-ac1f6b6435d0']),
  ('d04e054aefb94d93', ['000a6c98-bb9b-11e8-b2b9-ac1f6b6435d0']),
  ('c0dc5ccb97707433', ['000a9596-bbc4-11e8-b2bc-ac1f6b6435d0']),
  ('d10fe1897e5f6814', ['000c99ba-bba4-11e8-b2b9-ac1f6b6435d0']),
  ('8d35222a8d57f74c', ['001838f8-bbca-11e8-b2bc-ac1f6b6435d0'])])

In [44]:
with open('../cache/p2h_blue.pkl', 'wb') as f:
    pickle.dump(p2h_blue, f)
with open('../cache/h2ps_blue.pkl', 'wb') as f:
    pickle.dump(h2ps_blue, f)

In [18]:
h2ps_red_test = {}
len_ps = {}
for h, ps in tqdm_notebook(h2ps_red.items()):
    l = len(ps)
    if l not in len_ps: len_ps[l] = 1
    else: len_ps[l] = len_ps[l] + 1
    for p in ps:
        if p in submit:
            if h not in h2ps_red_test: h2ps_red_test[h] = []
            for p1 in ps:
                if p1 not in h2ps_red_test[h]: h2ps_red_test[h].append(p1)
            break
len(h2ps_red_test),list(h2ps_red_test.items())[:5]

HBox(children=(IntProgress(value=0, max=112818), HTML(value='')))

(11637,
 [('b4bf67d749840a70',
   ['31240_1645_E5_34', 'df533cce-bac7-11e8-b2b7-ac1f6b6435d0']),
  ('c6e3f2581e3c390d',
   ['35086_383_E8_7', '5661665e-bacf-11e8-b2b8-ac1f6b6435d0']),
  ('971e69cb1d652aa1',
   ['67932_1255_A3_4', '39508fe6-bad3-11e8-b2b8-ac1f6b6435d0']),
  ('a8b8ed3947310fb2',
   ['28911_692_A1_5', '3158d740-bad7-11e8-b2b9-ac1f6b6435d0']),
  ('d8a165561ebf80b9',
   ['43467_480_D6_2', 'fcd88d84-bad2-11e8-b2b8-ac1f6b6435d0'])])

In [19]:
len_ps

{1: 108304, 2: 4473, 3: 39, 4: 1, 9: 1}

In [20]:
list(h2ps_red_test.items())[:250]

[('b4bf67d749840a70',
  ['31240_1645_E5_34', 'df533cce-bac7-11e8-b2b7-ac1f6b6435d0']),
 ('c6e3f2581e3c390d',
  ['35086_383_E8_7', '5661665e-bacf-11e8-b2b8-ac1f6b6435d0']),
 ('971e69cb1d652aa1',
  ['67932_1255_A3_4', '39508fe6-bad3-11e8-b2b8-ac1f6b6435d0']),
 ('a8b8ed3947310fb2',
  ['28911_692_A1_5', '3158d740-bad7-11e8-b2b9-ac1f6b6435d0']),
 ('d8a165561ebf80b9',
  ['43467_480_D6_2', 'fcd88d84-bad2-11e8-b2b8-ac1f6b6435d0']),
 ('92531bfc694e6538',
  ['43467_480_D6_3', 'df8d2780-bac8-11e8-b2b8-ac1f6b6435d0']),
 ('8cca3b66cd498dd4',
  ['46572_901_E12_1', 'b5f922a4-bac6-11e8-b2b7-ac1f6b6435d0']),
 ('dcff5c7194210599',
  ['23620_387_F1_1', '4e10aecc-bacc-11e8-b2b8-ac1f6b6435d0']),
 ('d4d935ad3c661307',
  ['31107_583_E11_1', '72a6fbf8-bad4-11e8-b2b8-ac1f6b6435d0']),
 ('dce838e4f6d94886',
  ['1306_345_H10_4', '11107ebc-bac7-11e8-b2b7-ac1f6b6435d0']),
 ('db1aa18e7875c6b0',
  ['33874_932_G11_1', '7c1f771c-bac7-11e8-b2b7-ac1f6b6435d0']),
 ('ce7ea08189ef4955',
  ['33874_932_G11_2', 'af2c5f2e-bac9-

In [53]:
with open('../cache/h2ps_red_test.pkl', 'wb') as f:
    pickle.dump(h2ps_red_test, f)

In [29]:
h2ps_green_test = {}
for h, ps in tqdm_notebook(h2ps_green.items()):
    for p in ps:
        if p in submit:
            if h not in h2ps_green_test: h2ps_green_test[h] = []
            for p1 in ps:
                if p1 not in h2ps_green_test[h]: h2ps_green_test[h].append(p1)
            break
len(h2ps_green_test),list(h2ps_green_test.items())[:5]

HBox(children=(IntProgress(value=0, max=113051), HTML(value='')))

(11693,
 [('94bf63d619842e71',
   ['31240_1645_E5_34', 'df533cce-bac7-11e8-b2b7-ac1f6b6435d0']),
  ('cc73d2dc338c330d',
   ['35086_383_E8_7', '5661665e-bacf-11e8-b2b8-ac1f6b6435d0']),
  ('cc61720b78b72bc6',
   ['47377_688_E7_10', 'b029f372-bad9-11e8-b2b9-ac1f6b6435d0']),
  ('c9c86d2898d8faea',
   ['67932_1255_A3_4', '39508fe6-bad3-11e8-b2b8-ac1f6b6435d0']),
  ('9cfdad2942f10c72',
   ['28911_692_A1_5', '3158d740-bad7-11e8-b2b9-ac1f6b6435d0'])])

In [52]:
with open('../cache/h2ps_green_test.pkl', 'wb') as f:
    pickle.dump(h2ps_green_test, f)

In [30]:
h2ps_blue_test = {}
for h, ps in tqdm_notebook(h2ps_blue.items()):
    for p in ps:
        if p in submit:
            if h not in h2ps_blue_test: h2ps_blue_test[h] = []
            for p1 in ps:
                if p1 not in h2ps_blue_test[h]: h2ps_blue_test[h].append(p1)
            break
len(h2ps_blue_test),list(h2ps_blue_test.items())[:5]

HBox(children=(IntProgress(value=0, max=112455), HTML(value='')))

(11686,
 [('aa55aa55aa55aa55',
   ['c77f25e2-bbab-11e8-b2ba-ac1f6b6435d0',
    '8d5de5ec-bacf-11e8-b2b8-ac1f6b6435d0']),
  ('949b42d219d46ef5',
   ['31240_1645_E5_34', 'df533cce-bac7-11e8-b2b7-ac1f6b6435d0']),
  ('c6e3b2d83e2c390d',
   ['35086_383_E8_7', '5661665e-bacf-11e8-b2b8-ac1f6b6435d0']),
  ('934d1370bf478e70',
   ['63771_1414_D12_2', 'adc182fa-bad2-11e8-b2b8-ac1f6b6435d0']),
  ('cdc92f2ab1c1cec8',
   ['67932_1255_A3_4', '39508fe6-bad3-11e8-b2b8-ac1f6b6435d0'])])

In [51]:
with open('../cache/h2ps_blue_test.pkl', 'wb') as f:
    pickle.dump(h2ps_blue_test, f)

In [21]:
count = 0
for h, ps in tqdm_notebook(h2ps_red_test.items()):
    if len(ps) == 2:
        count += 1
print(count)

HBox(children=(IntProgress(value=0, max=11637), HTML(value='')))


181


In [22]:
len(tagged)

105678

In [23]:
train_p = list(tagged.keys())

In [27]:
red_test_ps = []
red_train_ps = []
for h, ps in tqdm_notebook(h2ps_red_test.items()):
    if len(ps) != 2:
#         print(h, ps)
        continue
    if ps[0] in train_p and ps[1] in submit:
        red_train_ps.append(ps[0])
        red_test_ps.append(ps[1])
    elif ps[1] in train_p and ps[0] in submit:
        red_train_ps.append(ps[1])
        red_test_ps.append(ps[0])
    else:
        print(h,ps)

HBox(children=(IntProgress(value=0, max=11637), HTML(value='')))

b213be247fd8470c ['00e00666-badb-11e8-b2b9-ac1f6b6435d0', '0cab24d6-bac6-11e8-b2b7-ac1f6b6435d0']
82a6c6ccabd3b872 ['013868ca-bad0-11e8-b2b8-ac1f6b6435d0', '9ba6f2d0-bac8-11e8-b2b8-ac1f6b6435d0']
e70a02c1f176be93 ['030580d8-bad6-11e8-b2b9-ac1f6b6435d0', 'f3910e40-bacd-11e8-b2b8-ac1f6b6435d0']
c03c8fee9130e9f2 ['0407cae4-bacd-11e8-b2b8-ac1f6b6435d0', '429149be-bad9-11e8-b2b9-ac1f6b6435d0']
c7057a1d5f388ab4 ['06efae44-bacc-11e8-b2b8-ac1f6b6435d0', '096d737c-bacc-11e8-b2b8-ac1f6b6435d0']
dc586b6b61b4c632 ['0774284e-bad7-11e8-b2b9-ac1f6b6435d0', '34aa05de-bad4-11e8-b2b8-ac1f6b6435d0']
ece70839396be207 ['08d495da-bad1-11e8-b2b8-ac1f6b6435d0', 'c0145aba-bac6-11e8-b2b7-ac1f6b6435d0']
81a9ad3ae879961d ['09b910ec-bac8-11e8-b2b7-ac1f6b6435d0', '66606722-bace-11e8-b2b8-ac1f6b6435d0']
aa90d6b91733a335 ['0bab42a8-bad2-11e8-b2b8-ac1f6b6435d0', '94e88a40-bacc-11e8-b2b8-ac1f6b6435d0']
9563398632740bef ['0c27d1d6-baca-11e8-b2b8-ac1f6b6435d0', '5b685d12-bad2-11e8-b2b8-ac1f6b6435d0']
83dd2e161978f073 ['1

In [25]:
len(red_test_ps), len(red_train_ps)

(120, 120)

In [36]:
green_test_ps = []
green_train_ps = []
for h, ps in tqdm_notebook(h2ps_green_test.items()):
    if len(ps) != 2:
        print(h, ps)
        continue
    if ps[0] in train_p and ps[1] in submit:
        green_train_ps.append(ps[0])
        green_test_ps.append(ps[1])
    elif ps[1] in train_p and ps[0] in submit:
        green_train_ps.append(ps[1])
        green_test_ps.append(ps[0])
    else:
        print(h, ps)

HBox(children=(IntProgress(value=0, max=11693), HTML(value='')))

ad91725e0ecc2b53 ['49352_927_F12_11', '2e2f56fa-bacf-11e8-b2b8-ac1f6b6435d0', '3323fc06-bad4-11e8-b2b8-ac1f6b6435d0']
9fb3521188bf4f42 ['00008af0-bad0-11e8-b2b8-ac1f6b6435d0']
c03d2fc36d7433c1 ['0000a892-bacf-11e8-b2b8-ac1f6b6435d0']
8ef1420b1798ef71 ['0006faa6-bac7-11e8-b2b7-ac1f6b6435d0']
c313e7e307d2c34c ['0008baca-bad7-11e8-b2b9-ac1f6b6435d0']
c3c51e1a70369fe4 ['000cce7e-bad4-11e8-b2b8-ac1f6b6435d0']
85d878a5c69ba30f ['00109f6a-bac8-11e8-b2b7-ac1f6b6435d0']
d9532e087caf61cc ['001765de-bacd-11e8-b2b8-ac1f6b6435d0']
bcdee692090956ab ['0018641a-bac9-11e8-b2b8-ac1f6b6435d0']
857a44a958e759a7 ['00200f22-bad7-11e8-b2b9-ac1f6b6435d0']
a79b5070af86d239 ['0026f154-bac6-11e8-b2b7-ac1f6b6435d0']
eaeaeeaa1f113150 ['002729d2-bace-11e8-b2b8-ac1f6b6435d0']
d826398d73076f98 ['002c1a7c-bad4-11e8-b2b8-ac1f6b6435d0']
e36320cb53fe5815 ['003170fa-bacd-11e8-b2b8-ac1f6b6435d0']
c7c404fb1a436f9c ['0031820a-baca-11e8-b2b8-ac1f6b6435d0']
f3bff0d25600126d ['00407c16-bad3-11e8-b2b8-ac1f6b6435d0']
b775b5a1a484

a93f75f0121e628d ['0c1a2d0c-bace-11e8-b2b8-ac1f6b6435d0']
d89b324c417b5e74 ['0c1dc0c4-baca-11e8-b2b8-ac1f6b6435d0']
d06e914f1ffd420c ['0c1effb2-bac9-11e8-b2b8-ac1f6b6435d0']
c502e18f7ed8e94c ['0c258434-bada-11e8-b2b9-ac1f6b6435d0']
926d9b5268c293af ['0c271aa6-bad0-11e8-b2b8-ac1f6b6435d0']
90c38ca63ee636dc ['0c27d1d6-baca-11e8-b2b8-ac1f6b6435d0', '5b685d12-bad2-11e8-b2b8-ac1f6b6435d0']
acd4ae50a117eaf4 ['0c31bf22-bad7-11e8-b2b9-ac1f6b6435d0']
823770ae235bc3ea ['0c35b304-bad5-11e8-b2b8-ac1f6b6435d0']
99673c13c538c69b ['0c38226a-bad0-11e8-b2b8-ac1f6b6435d0']
9c4d62c41c6bf72c ['0c3c57fe-bac6-11e8-b2b7-ac1f6b6435d0']
ac13cc3b66bd61c8 ['0c4035e4-bad6-11e8-b2b9-ac1f6b6435d0']
92446d99b626db36 ['0c43a180-bada-11e8-b2b9-ac1f6b6435d0']
b7e2aa5e393f1a00 ['0c495f86-bacf-11e8-b2b8-ac1f6b6435d0']
c98c03acb21d7b75 ['0c5847ca-bad0-11e8-b2b8-ac1f6b6435d0']
d9969ad8d3663226 ['0c59923c-badb-11e8-b2b9-ac1f6b6435d0']
dd333a4d1f7000f6 ['0c5aae60-badb-11e8-b2b9-ac1f6b6435d0']
aaab4ae0b545495f ['0c5b9b12-bacd

f4c4bc1b43f41a9c ['2280fd8c-bad3-11e8-b2b8-ac1f6b6435d0']
e06ef07d58aa0f43 ['2285a2a2-bad7-11e8-b2b9-ac1f6b6435d0']
c5bc1a4a7a63e135 ['2288ac22-bacd-11e8-b2b8-ac1f6b6435d0']
c8743be34e99523c ['2298ed50-bac6-11e8-b2b7-ac1f6b6435d0']
abf33834c84616bd ['229f960a-bada-11e8-b2b9-ac1f6b6435d0']
d76104fe6470ce3c ['22a3dc20-bad4-11e8-b2b8-ac1f6b6435d0']
e6da689da91798a2 ['22a542b2-bad5-11e8-b2b8-ac1f6b6435d0']
81c45e9b2974d3b6 ['22aee4c6-bad4-11e8-b2b8-ac1f6b6435d0']
ae4972327256a59b ['22b0eed8-baca-11e8-b2b8-ac1f6b6435d0']
da6b943be0b8e01e ['22b48912-bacf-11e8-b2b8-ac1f6b6435d0']
c01afe355f58b826 ['22b63be2-bac8-11e8-b2b7-ac1f6b6435d0']
92d127e56d0b7278 ['22b6cb28-baca-11e8-b2b8-ac1f6b6435d0']
b122b29d765b4c36 ['22b88cee-bac8-11e8-b2b7-ac1f6b6435d0']
d845262b7db40f53 ['22b9506c-bac7-11e8-b2b7-ac1f6b6435d0']
cc4333734cccfc0b ['22bd4e28-bad7-11e8-b2b9-ac1f6b6435d0']
a756844fc098edf8 ['22c46b68-bad2-11e8-b2b8-ac1f6b6435d0']
eb9b152c148d4e3e ['22c9913c-bac9-11e8-b2b8-ac1f6b6435d0']
c824ebe0b654e7

8b9b45e32ae3329a ['33bd8638-bad3-11e8-b2b8-ac1f6b6435d0']
aeaa39ba8bab301a ['33be4b6c-bad4-11e8-b2b8-ac1f6b6435d0']
8396c95a5ca9a3f2 ['33bfa2ea-bada-11e8-b2b9-ac1f6b6435d0']
cae170e00e7c1f8f ['33c714bc-bada-11e8-b2b9-ac1f6b6435d0']
d76036cf31f68033 ['33cab936-bad1-11e8-b2b8-ac1f6b6435d0']
e38571788e6c55e1 ['33d6b10e-bacd-11e8-b2b8-ac1f6b6435d0']
9bd4d754f660e0c8 ['33dcd60e-baca-11e8-b2b8-ac1f6b6435d0']
f8ad9b55722723c0 ['33f46de2-bace-11e8-b2b8-ac1f6b6435d0']
c1c72d071b974ee1 ['33fe5e38-bad8-11e8-b2b9-ac1f6b6435d0']
d7e3098a21707e1f ['34081b80-bad8-11e8-b2b9-ac1f6b6435d0']
ded75a36096086f8 ['34118896-bac9-11e8-b2b8-ac1f6b6435d0']
f9de5a31a3c21e0c ['341dc3b4-bad2-11e8-b2b8-ac1f6b6435d0']
96189b9273933f68 ['341f6caa-bacd-11e8-b2b8-ac1f6b6435d0']
f3d1615793c9f480 ['34203822-bad9-11e8-b2b9-ac1f6b6435d0']
e23ae0ee03fc3ec0 ['3420c44e-bad0-11e8-b2b8-ac1f6b6435d0']
b90ab4053f2177e3 ['34237b30-bacb-11e8-b2b8-ac1f6b6435d0']
ac136eae37f8054a ['3427fae8-bad0-11e8-b2b8-ac1f6b6435d0']
86b9da48dea438

...

a97bc54716b108dd ['a6ecea5c-bac6-11e8-b2b7-ac1f6b6435d0']
c9c0377700dfb81e ['a6fe64e6-bac9-11e8-b2b8-ac1f6b6435d0']
889bb3ae2c6c2e66 ['a7005d26-bad0-11e8-b2b8-ac1f6b6435d0']
d4dc4881f9f2b661 ['a7122c0c-bac8-11e8-b2b8-ac1f6b6435d0']
c5b911a5bf1b182d ['a7124fe6-bac5-11e8-b2b7-ac1f6b6435d0']
d26d3067cc31db34 ['a721e0ce-bac9-11e8-b2b8-ac1f6b6435d0']
e262b3cd2c95321f ['a72ba9e2-bac9-11e8-b2b8-ac1f6b6435d0']
b5c9966ad668f206 ['a72c296a-bada-11e8-b2b9-ac1f6b6435d0']
c712316bd95761cc ['a7349c08-bacb-11e8-b2b8-ac1f6b6435d0']
f85702eb05c8b75a ['a7372660-bacd-11e8-b2b8-ac1f6b6435d0']
958784ff782cec28 ['a738102e-bace-11e8-b2b8-ac1f6b6435d0']
933c2e26c886973f ['a73f022e-bad5-11e8-b2b9-ac1f6b6435d0']
b69759819c3e8c47 ['a742f28a-bac6-11e8-b2b7-ac1f6b6435d0']
d0cd9b2d6e89389a ['a7446926-bad5-11e8-b2b9-ac1f6b6435d0']
f8d9ac499c4e3269 ['a749279a-bad5-11e8-b2b9-ac1f6b6435d0']
c9354087687e9f33 ['a74b4ec6-bad0-11e8-b2b8-ac1f6b6435d0']
8140786d1acf3ebd ['a74c5fa2-bac9-11e8-b2b8-ac1f6b6435d0']
d86736e81f8963

bd86e7c2413f7064 ['c2b96eda-bad1-11e8-b2b8-ac1f6b6435d0']
a5600a5cfd138fb3 ['c2bca628-bac6-11e8-b2b7-ac1f6b6435d0']
8b33c22c33ce39d3 ['c2bf4952-bad8-11e8-b2b9-ac1f6b6435d0']
c4dbef714a108b66 ['c2c29d2c-bac5-11e8-b2b7-ac1f6b6435d0']
885dd3036767cd46 ['c2c2beaa-bac6-11e8-b2b7-ac1f6b6435d0']
85ea05e88fd0bb71 ['c2c499dc-bad5-11e8-b2b9-ac1f6b6435d0']
91ce76d2efe01a41 ['c2c657e4-bac7-11e8-b2b7-ac1f6b6435d0']
95c3d1c5f4ba2a2c ['c2c6b49e-bad3-11e8-b2b8-ac1f6b6435d0']
a5951f616eca4b29 ['c2c7ff32-bad5-11e8-b2b9-ac1f6b6435d0']
9dcb3531f2a46a2c ['c2cdc664-bad1-11e8-b2b8-ac1f6b6435d0']
8c4c081f9b235bdf ['c2d230be-bacc-11e8-b2b8-ac1f6b6435d0']
bdda57876a8f1804 ['c2d3a54c-bac8-11e8-b2b8-ac1f6b6435d0']
a5ecb6c0e97a3981 ['c2e4bcea-bad9-11e8-b2b9-ac1f6b6435d0']
cfc735d0b06dcb20 ['c2ebb21c-bace-11e8-b2b8-ac1f6b6435d0']
9b642bdc36c13ec1 ['c2ebdb64-bacb-11e8-b2b8-ac1f6b6435d0']
d410741e70cff399 ['c2ecdcf0-bad3-11e8-b2b8-ac1f6b6435d0']
e89492fb1f492578 ['c2f3fbb0-bacf-11e8-b2b8-ac1f6b6435d0']
91f20d1cf6276c

dc8d3988ceb3b107 ['cd7a3216-bac5-11e8-b2b7-ac1f6b6435d0']
acd4f0f7a28b5a41 ['cd80655e-bad0-11e8-b2b8-ac1f6b6435d0']
cc903e4d9fc6684e ['cd83820a-bad2-11e8-b2b8-ac1f6b6435d0']
8bcf1823bb6407b9 ['cd8b2ab8-bad3-11e8-b2b8-ac1f6b6435d0']
a8d0a333978b565b ['cd915274-bada-11e8-b2b9-ac1f6b6435d0']
d05eeb1e213299b6 ['cd96f408-bad6-11e8-b2b9-ac1f6b6435d0']
926f1909b4cec1fc ['cda86f40-bad5-11e8-b2b9-ac1f6b6435d0']
f00f709dc77a3914 ['cdaf4e2e-bad9-11e8-b2b9-ac1f6b6435d0']
9393696c261f59d8 ['cdb72b0e-bace-11e8-b2b8-ac1f6b6435d0']
c1792b436c96798d ['cdc42d02-bad5-11e8-b2b9-ac1f6b6435d0']
910b0bb6f20f26f9 ['cdd31e5a-bac8-11e8-b2b8-ac1f6b6435d0']
fc310eedd3840ed8 ['cdd60d42-bad5-11e8-b2b9-ac1f6b6435d0']
d62f09f6932e6889 ['cdd83750-bac8-11e8-b2b8-ac1f6b6435d0']
e4f1f00f0f1b0e5a ['cdd96512-bad7-11e8-b2b9-ac1f6b6435d0']
a1221b9e7f729558 ['cdda98c0-bad6-11e8-b2b9-ac1f6b6435d0']
85f846521325ebdb ['cddaf9b2-bad3-11e8-b2b8-ac1f6b6435d0']
fe9828e5fcde8011 ['cddd9b0c-bad0-11e8-b2b8-ac1f6b6435d0']
edc4a223b7b186

c35996198c79d639 ['e9d9e8ec-bad0-11e8-b2b8-ac1f6b6435d0']
c7d4b82cc33b74c1 ['e9db58b4-bad3-11e8-b2b8-ac1f6b6435d0']
d3ab8389221e797c ['e9e89736-bad3-11e8-b2b8-ac1f6b6435d0']
8c8b47e22b8c793d ['e9f21556-bad6-11e8-b2b9-ac1f6b6435d0']
a87bcf5b57847028 ['e9f4aa3c-bacc-11e8-b2b8-ac1f6b6435d0']
f35ed005030f33ed ['e9fd33c4-bada-11e8-b2b9-ac1f6b6435d0']
d28aa0e7d228ded3 ['ea022f96-bada-11e8-b2b9-ac1f6b6435d0']
d51718b2ade53570 ['ea037202-bad0-11e8-b2b8-ac1f6b6435d0']
958e6ad50593b49e ['ea04619a-bad9-11e8-b2b9-ac1f6b6435d0']
d54c33d2c698ad96 ['ea0475bc-bacb-11e8-b2b8-ac1f6b6435d0']
90d6352833579c3f ['ea121a46-bad0-11e8-b2b8-ac1f6b6435d0']
a48c55bf85f139a1 ['ea1a2cea-bac6-11e8-b2b7-ac1f6b6435d0']
afd51816773c70c2 ['ea1d489a-bacf-11e8-b2b8-ac1f6b6435d0']
f50ee41d2568df81 ['ea2152be-bac5-11e8-b2b7-ac1f6b6435d0']
99e5a0f4b86cec62 ['ea22896e-bad3-11e8-b2b8-ac1f6b6435d0']
dd0ddf2c0219e578 ['ea2c9a5a-bad1-11e8-b2b8-ac1f6b6435d0']
895732a5e50c2ebe ['ea2f8956-bad4-11e8-b2b8-ac1f6b6435d0']
ce07d2c516e792

8b64d8ae55a86ad5 ['f4d43f74-bac9-11e8-b2b8-ac1f6b6435d0']
d917293e622ecd61 ['f4df020e-bacb-11e8-b2b8-ac1f6b6435d0']
c1c57a3b5439f885 ['f4ea734a-bac7-11e8-b2b7-ac1f6b6435d0']
8695c0c6d4a5c3fb ['f4ec70de-baca-11e8-b2b8-ac1f6b6435d0']
d028666d60fdc697 ['f4f6cdfc-bac7-11e8-b2b7-ac1f6b6435d0']
c4b938ec93d13d86 ['f4f98044-bacf-11e8-b2b8-ac1f6b6435d0']
d227fb86c0303bec ['f4ff1d32-bad5-11e8-b2b9-ac1f6b6435d0']
b519e26d41da6dc2 ['f5011164-bada-11e8-b2b9-ac1f6b6435d0']
861c6f611bd2b387 ['f5056cdc-bacb-11e8-b2b8-ac1f6b6435d0']
81153a5efaf0a3b1 ['f5098f5e-bac8-11e8-b2b8-ac1f6b6435d0']
db30609f3348fce1 ['f50a2e9c-bad6-11e8-b2b9-ac1f6b6435d0']
88cc0dfd562e2a5b ['f52160c2-bada-11e8-b2b9-ac1f6b6435d0']
89359e53de1b60c3 ['f5293884-bad4-11e8-b2b8-ac1f6b6435d0']
c95369365aa5d3c2 ['f52d0da2-bace-11e8-b2b8-ac1f6b6435d0']
92645a2edd78d296 ['f5409226-bacb-11e8-b2b8-ac1f6b6435d0']
9bf10afb162f7044 ['f5418e22-bacd-11e8-b2b8-ac1f6b6435d0']
c6232dbc4f1e07b1 ['f5468602-bacd-11e8-b2b8-ac1f6b6435d0']
cc63f917bd009e

In [37]:
len(green_test_ps), len(green_train_ps)

(141, 141)

In [38]:
blue_test_ps = []
blue_train_ps = []
for h, ps in tqdm_notebook(h2ps_blue_test.items()):
    if len(ps) != 2:
        print(h, ps)
        continue
    if ps[0] in train_p and ps[1] in submit:
        blue_train_ps.append(ps[0])
        blue_test_ps.append(ps[1])
    elif ps[1] in train_p and ps[0] in submit:
        blue_train_ps.append(ps[1])
        blue_test_ps.append(ps[0])
    else:
        print(h, ps)

HBox(children=(IntProgress(value=0, max=11686), HTML(value='')))

ad11725e0eec2b53 ['49352_927_F12_11', '2e2f56fa-bacf-11e8-b2b8-ac1f6b6435d0', '3323fc06-bad4-11e8-b2b8-ac1f6b6435d0']
df31da2184394f72 ['00008af0-bad0-11e8-b2b8-ac1f6b6435d0']
c11c6ee36534b3c5 ['0000a892-bacf-11e8-b2b8-ac1f6b6435d0']
8c73cf8b178cca43 ['0006faa6-bac7-11e8-b2b7-ac1f6b6435d0']
c313e5e503d3d34c ['0008baca-bad7-11e8-b2b9-ac1f6b6435d0']
c7cc1e73303f46c4 ['000cce7e-bad4-11e8-b2b8-ac1f6b6435d0']
86f238ad869a334f ['00109f6a-bac8-11e8-b2b7-ac1f6b6435d0']
d9772e4974be4109 ['001765de-bacd-11e8-b2b8-ac1f6b6435d0']
989d66968969726b ['0018641a-bac9-11e8-b2b8-ac1f6b6435d0']
c53344a9d82739cf ['00200f22-bad7-11e8-b2b9-ac1f6b6435d0']
d27f8c9e51818ae3 ['0026f154-bac6-11e8-b2b7-ac1f6b6435d0']
aaaaaaaa0f175555 ['002729d2-bace-11e8-b2b8-ac1f6b6435d0']
eb0101cf5b3746bc ['002c1a7c-bad4-11e8-b2b8-ac1f6b6435d0']
e22321cf43d7ca55 ['003170fa-bacd-11e8-b2b8-ac1f6b6435d0']
966409f37a4b6d98 ['0031820a-baca-11e8-b2b8-ac1f6b6435d0']
a1bf96d21ec1a10f ['00407c16-bad3-11e8-b2b8-ac1f6b6435d0']
ae35a5a5ad25

810edc98b3f56599 ['1b586b1e-bad6-11e8-b2b9-ac1f6b6435d0']
c83b640fceb16b8c ['1b65c3be-bad0-11e8-b2b8-ac1f6b6435d0']
b91fa047987ee20e ['1b694598-bacb-11e8-b2b8-ac1f6b6435d0']
c76b9c2b54219f94 ['1b802f10-bada-11e8-b2b9-ac1f6b6435d0']
e8e45cbe4ec0f0a9 ['1b84e120-bad2-11e8-b2b8-ac1f6b6435d0']
8c73894e63dc33cc ['1b963392-bad9-11e8-b2b9-ac1f6b6435d0']
c0133f6c678fc2b2 ['1ba31254-bacc-11e8-b2b8-ac1f6b6435d0']
ea0405bee61fc599 ['1ba467b4-bad4-11e8-b2b8-ac1f6b6435d0']
ad5ab4aaf351a581 ['1ba86c66-bac9-11e8-b2b8-ac1f6b6435d0']
ccc663253db89c2d ['1ba96cb0-bace-11e8-b2b8-ac1f6b6435d0']
cdca3538d1e3065e ['1bab8292-bacf-11e8-b2b8-ac1f6b6435d0']
cc3107ff01e0fc33 ['1bad8b2a-bad2-11e8-b2b8-ac1f6b6435d0']
d54f810a9d0cadf6 ['1bb0d9dc-bad3-11e8-b2b8-ac1f6b6435d0']
d7c369057c13276c ['1bb1edf0-bad2-11e8-b2b8-ac1f6b6435d0']
c1e26c1f3e1d62d1 ['1bb67ee0-bacf-11e8-b2b8-ac1f6b6435d0']
c81c648f3333aff0 ['1bb72d48-badb-11e8-b2b9-ac1f6b6435d0']
d3ddcde21a0e48d2 ['1bbe56a8-bac8-11e8-b2b7-ac1f6b6435d0']
d3873d106e81de

c3e33826939b7cb0 ['2c2200d0-bac8-11e8-b2b7-ac1f6b6435d0']
92dc51472b9176cd ['2c24230c-bacc-11e8-b2b8-ac1f6b6435d0']
d3db242626c3c3d9 ['2c352b56-bac8-11e8-b2b7-ac1f6b6435d0']
934b6eac19d03c9e ['2c40f510-bad9-11e8-b2b9-ac1f6b6435d0']
8c9cae773a47609c ['2c4139e6-bac8-11e8-b2b7-ac1f6b6435d0']
d1a559be824b963c ['2c478362-baca-11e8-b2b8-ac1f6b6435d0']
a77c50ee1415ba87 ['2c49d56e-bad3-11e8-b2b8-ac1f6b6435d0']
ac8e86e6ae8e8e8c ['2c55688e-bac9-11e8-b2b8-ac1f6b6435d0']
80cb75d436b89a37 ['2c5704f4-bad9-11e8-b2b9-ac1f6b6435d0']
a5ec58851ecccd78 ['2c57c900-bad1-11e8-b2b8-ac1f6b6435d0']
eb1055e42ea7885f ['2c5e4e24-bac7-11e8-b2b7-ac1f6b6435d0']
db5fb245c01d388b ['2c69c19e-bac9-11e8-b2b8-ac1f6b6435d0']
e1a52770cf1e5878 ['2c8ef12a-bad4-11e8-b2b8-ac1f6b6435d0']
c1ec3923c780eccf ['2c909ca0-baca-11e8-b2b8-ac1f6b6435d0']
973877942e90d78c ['2c91cbfe-bacd-11e8-b2b8-ac1f6b6435d0']
ca3669c5cd1a33e1 ['2c9c234a-bad4-11e8-b2b8-ac1f6b6435d0']
fe9ba272e8101fa4 ['2c9f1aa0-bacf-11e8-b2b8-ac1f6b6435d0']
9cd6dc3332722d

d9c63660b31b5a71 ['43766f4a-bac9-11e8-b2b8-ac1f6b6435d0']
9478b6585a966ec3 ['43771fc4-bada-11e8-b2b9-ac1f6b6435d0']
a4ae5d7aa41b0a5d ['437aa498-bace-11e8-b2b8-ac1f6b6435d0']
cd0e05dd58832afb ['437d8bd4-bad0-11e8-b2b8-ac1f6b6435d0']
867d6233e945b18d ['4383fb60-bace-11e8-b2b8-ac1f6b6435d0']
d0701b4f3dd2c4f1 ['4384013e-bad6-11e8-b2b9-ac1f6b6435d0']
81187d3c72c6799b ['4385b20a-bad5-11e8-b2b9-ac1f6b6435d0']
dc5d2439f79a0964 ['43889e8e-bacb-11e8-b2b8-ac1f6b6435d0']
913e639c36c318f3 ['438f8738-bad7-11e8-b2b9-ac1f6b6435d0']
cf337acc21dc5033 ['43948444-bad8-11e8-b2b9-ac1f6b6435d0']
c62fd2e1076146b7 ['439e4edc-bacb-11e8-b2b8-ac1f6b6435d0']
91b212cf6cc1a57e ['43a8f830-bad2-11e8-b2b8-ac1f6b6435d0']
93e4649d0f9f1c4a ['43aa85e6-bad3-11e8-b2b8-ac1f6b6435d0']
8e4ca13f572929e3 ['43b122d6-bad6-11e8-b2b9-ac1f6b6435d0']
d59b237062b5e833 ['43ba06e0-bad0-11e8-b2b8-ac1f6b6435d0']
d43398ea81b479f1 ['43be0ee2-bac7-11e8-b2b7-ac1f6b6435d0']
cc2d33c44e72f18d ['43c3dc12-bac9-11e8-b2b8-ac1f6b6435d0']
b2554f8a6996a6

...

cc370fc04f394b0f ['9ff212e8-bad2-11e8-b2b8-ac1f6b6435d0']
8357789718b9cb94 ['9ffbc074-bac6-11e8-b2b7-ac1f6b6435d0']
d326fd87e8039ac4 ['a00566bc-bad3-11e8-b2b8-ac1f6b6435d0']
b5a9d85a5a68f245 ['a0137418-bac5-11e8-b2b7-ac1f6b6435d0']
8c69b6259a4eb5d8 ['a0234ad6-bada-11e8-b2b9-ac1f6b6435d0']
c33b6ab8839cf28a ['a02db460-bad7-11e8-b2b9-ac1f6b6435d0']
83ed9ded36036072 ['a02fa092-bada-11e8-b2b9-ac1f6b6435d0']
b78d406b3e64aa6a ['a030d310-bac9-11e8-b2b8-ac1f6b6435d0']
ca0683fd0dd1b3d1 ['a031d9ec-bacc-11e8-b2b8-ac1f6b6435d0']
e7147a2a14ff01d5 ['a041062a-bac6-11e8-b2b7-ac1f6b6435d0']
8704d7a4ca27b54f ['a0529814-bac5-11e8-b2b7-ac1f6b6435d0']
d07c278778f11c0f ['a0621e78-bad5-11e8-b2b9-ac1f6b6435d0']
8bdb518389295cfc ['a063537e-bada-11e8-b2b9-ac1f6b6435d0']
dcf14e2c585663e4 ['a0649ef6-bad9-11e8-b2b9-ac1f6b6435d0']
894e5877e64aa91d ['a06fbbb6-bad8-11e8-b2b9-ac1f6b6435d0']
ac0f1a7f0957ce42 ['a071d974-bad7-11e8-b2b9-ac1f6b6435d0']
9b2870c19d3e64db ['a0735f9a-baca-11e8-b2b8-ac1f6b6435d0']
e31ce233af154c

c2352fd69a6586f0 ['bbfeabf8-bad3-11e8-b2b8-ac1f6b6435d0']
993e59b3264923dc ['bbfecc00-bad8-11e8-b2b9-ac1f6b6435d0']
da4733ec803c77c1 ['bc09617a-bacd-11e8-b2b8-ac1f6b6435d0']
934f5477b449a44e ['bc0b8c64-baca-11e8-b2b8-ac1f6b6435d0']
f6d25eb6b1013d05 ['bc176ecc-bad8-11e8-b2b9-ac1f6b6435d0']
c5bc26244e4b6f39 ['bc23b558-bad1-11e8-b2b8-ac1f6b6435d0']
d82664b6145cde75 ['bc32dcee-bad2-11e8-b2b8-ac1f6b6435d0']
c21e7ce18fd03b2c ['bc389b08-bad1-11e8-b2b8-ac1f6b6435d0']
c46b373971c4cd26 ['bc3d4b7a-bad7-11e8-b2b9-ac1f6b6435d0']
d4702ccd971a8f87 ['bc43a69a-bac9-11e8-b2b8-ac1f6b6435d0']
93d62425dfed1232 ['bc4ce888-bad6-11e8-b2b9-ac1f6b6435d0']
996762d9269d5239 ['bc4fb6b0-bace-11e8-b2b8-ac1f6b6435d0']
92337cc44fb91b4c ['bc52c0b8-bac8-11e8-b2b8-ac1f6b6435d0']
93e5649a1e0f1e1e ['bc550e6e-bad6-11e8-b2b9-ac1f6b6435d0']
c1d883b65cc736a5 ['bc58fb08-bad8-11e8-b2b9-ac1f6b6435d0']
d4752d932a6a168f ['bc5cc49e-bad9-11e8-b2b9-ac1f6b6435d0']
c6c6360f4743b9e4 ['bc6035d8-bac6-11e8-b2b7-ac1f6b6435d0']
cb8c6cd80ee3a3

9d6e6601697968da ['cbf31b4a-bacc-11e8-b2b8-ac1f6b6435d0']
b66c643395d5c83a ['cbf78f0c-bac9-11e8-b2b8-ac1f6b6435d0']
cd736c662399125b ['cbfc8ef2-bad4-11e8-b2b8-ac1f6b6435d0']
89e443b5ee99514b ['cc0b9a20-bad7-11e8-b2b9-ac1f6b6435d0']
e8eb3f70563f2500 ['cc11da28-bac5-11e8-b2b7-ac1f6b6435d0']
d3893b65649a8799 ['cc146f56-bad7-11e8-b2b9-ac1f6b6435d0']
81776cd6229f224f ['cc154654-bad4-11e8-b2b8-ac1f6b6435d0']
ece0e1050706f5f7 ['cc166774-bad3-11e8-b2b8-ac1f6b6435d0']
cbd3381867e76324 ['cc19e6e2-bac9-11e8-b2b8-ac1f6b6435d0']
b935ac539a566a52 ['cc24ebb0-bad7-11e8-b2b9-ac1f6b6435d0']
a5a5a9a5a5ad6945 ['cc27bc24-bac7-11e8-b2b7-ac1f6b6435d0']
91716eb55b2c2479 ['cc2cf0f8-bacd-11e8-b2b8-ac1f6b6435d0']
b4b56852b2566e65 ['cc358864-bacb-11e8-b2b8-ac1f6b6435d0']
95264f953575d628 ['cc3ae1e2-bac6-11e8-b2b7-ac1f6b6435d0']
8d246b1dc05bf723 ['cc42b63a-bace-11e8-b2b8-ac1f6b6435d0']
91122d5e235cfbe8 ['cc44a5a2-baca-11e8-b2b8-ac1f6b6435d0']
e84b6f33164c358b ['cc496ebc-bad8-11e8-b2b9-ac1f6b6435d0']
85ce4f95755156

9b036d5c173ae525 ['f37b4dee-bad7-11e8-b2b9-ac1f6b6435d0']
bc35546086d379da ['f38adcbc-bad4-11e8-b2b8-ac1f6b6435d0']
aac35641f534b25b ['f3910e40-bacd-11e8-b2b8-ac1f6b6435d0']
cf9b12911f79a889 ['f3a8c7c2-bad9-11e8-b2b9-ac1f6b6435d0']
d2377327c4324799 ['f3b19b56-bacd-11e8-b2b8-ac1f6b6435d0']
e51f4299d6348fd0 ['f3b4a23e-bad6-11e8-b2b9-ac1f6b6435d0']
f4905a6761c94abd ['f3b5932a-bad5-11e8-b2b9-ac1f6b6435d0']
8b01b55e83f067e5 ['f3ba62e0-bad7-11e8-b2b9-ac1f6b6435d0']
f40f103fa3c05fd2 ['f3c9a804-bacd-11e8-b2b8-ac1f6b6435d0']
ce77198451c96778 ['f3ca1ffc-bac6-11e8-b2b7-ac1f6b6435d0']
a5b5174a4a4a4f4f ['f3d80900-bacb-11e8-b2b8-ac1f6b6435d0']
d19469b9a4e3b2d1 ['f3d8da94-bad8-11e8-b2b9-ac1f6b6435d0']
e905db7815a6554b ['f3da9e6c-bac7-11e8-b2b7-ac1f6b6435d0']
926992ff69b66d00 ['f3dae440-bacb-11e8-b2b8-ac1f6b6435d0']
c0700fbe69957639 ['f3e1e6e6-bac6-11e8-b2b7-ac1f6b6435d0']
bde9d5b3289052e8 ['f3e8f758-bad3-11e8-b2b8-ac1f6b6435d0']
d2780d8d7363cd62 ['f3ee0e50-bace-11e8-b2b8-ac1f6b6435d0']
ac126f655d48b5

841f665b38633bcc ['f8d314f6-bace-11e8-b2b8-ac1f6b6435d0']
8721f72d6ab6af00 ['f8e01cac-bad6-11e8-b2b9-ac1f6b6435d0']
c12f32cd22dd1be4 ['f8ea2aaa-bad9-11e8-b2b9-ac1f6b6435d0']
c63d18c7132acb73 ['f8ef80fe-bacf-11e8-b2b8-ac1f6b6435d0']
84eba148b579f662 ['f8efcc88-bad1-11e8-b2b8-ac1f6b6435d0']
9b6489667a5d1699 ['f8f224b2-bad9-11e8-b2b9-ac1f6b6435d0']
84677132da6d3966 ['f8f8b658-bacd-11e8-b2b8-ac1f6b6435d0']
9f652466315ad335 ['f9001386-bad1-11e8-b2b8-ac1f6b6435d0']
aeab0816743c79cd ['f9010f54-bad4-11e8-b2b8-ac1f6b6435d0']
d3702ccdc934971b ['f902691c-bad4-11e8-b2b8-ac1f6b6435d0']
ce86d2fb007fe502 ['f904ede4-bac6-11e8-b2b7-ac1f6b6435d0']
d43f69e0893b16f0 ['f9072da0-bacd-11e8-b2b8-ac1f6b6435d0']
ceb34634e7c4318d ['f90f53ec-bada-11e8-b2b9-ac1f6b6435d0']
cf237007e6f53c0c ['f913e764-baca-11e8-b2b8-ac1f6b6435d0']
9b2643f29a41b9f4 ['f91600dc-bacd-11e8-b2b8-ac1f6b6435d0']
c7d656bd64e21a18 ['f91d1342-bada-11e8-b2b9-ac1f6b6435d0']
89d0d9952e957672 ['f9315ea4-bad7-11e8-b2b9-ac1f6b6435d0']
c338e1d1f39866

In [39]:
len(blue_test_ps), len(blue_train_ps)

(159, 159)

In [40]:
test_ps = red_test_ps + green_test_ps + blue_test_ps
train_ps = red_train_ps + green_train_ps + blue_train_ps

In [41]:
len(test_ps), len(train_ps)

(420, 420)

In [42]:
df = pd.DataFrame()
df['test_id'] = test_ps
df['train_id'] = train_ps

In [43]:
df.head(), df.shape

(                                test_id          train_id
 0  df533cce-bac7-11e8-b2b7-ac1f6b6435d0  31240_1645_E5_34
 1  5661665e-bacf-11e8-b2b8-ac1f6b6435d0    35086_383_E8_7
 2  39508fe6-bad3-11e8-b2b8-ac1f6b6435d0   67932_1255_A3_4
 3  3158d740-bad7-11e8-b2b9-ac1f6b6435d0    28911_692_A1_5
 4  fcd88d84-bad2-11e8-b2b8-ac1f6b6435d0    43467_480_D6_2, (420, 2))

In [44]:
df = df.drop_duplicates()

In [45]:
df.shape

(215, 2)

In [46]:
df['Target'] = df['train_id'].map(lambda x: tagged[x])

In [47]:
df.head()

test_id          train_id    Target
0  df533cce-bac7-11e8-b2b7-ac1f6b6435d0  31240_1645_E5_34     18 17
1  5661665e-bacf-11e8-b2b8-ac1f6b6435d0    35086_383_E8_7   25 17 0
2  39508fe6-bad3-11e8-b2b8-ac1f6b6435d0   67932_1255_A3_4      16 0
3  3158d740-bad7-11e8-b2b9-ac1f6b6435d0    28911_692_A1_5      14 0
4  fcd88d84-bad2-11e8-b2b8-ac1f6b6435d0    43467_480_D6_2  16 25 14

In [48]:
df[['test_id', 'Target']].to_csv('../cache/leak2.csv', index=False)

In [49]:
df_leak = pd.read_csv('../cache/leak_test.csv')

In [50]:
df_leak.head()

Id   Target
0  7729b27c-bacc-11e8-b2b8-ac1f6b6435d0  25 18 0
1  5661665e-bacf-11e8-b2b8-ac1f6b6435d0  25 17 0
2  b029f372-bad9-11e8-b2b9-ac1f6b6435d0     23 2
3  adc182fa-bad2-11e8-b2b8-ac1f6b6435d0  23 0 21
4  39508fe6-bad3-11e8-b2b8-ac1f6b6435d0     16 0

In [51]:
s1 = set(df.test_id.values)
s2 = set(df_leak.Id.values)
s = s1.intersection(s2)
len(s)

214

In [96]:
len(df_leak)

259

In [43]:
match_vals = {}
for ii in tqdm_notebook(submit):
    h1 = p2h_red[ii]
    match_vals[ii] = []
    for jj in (tagged):
        h2 = p2h_red[jj]
        a = match(h1, h2, h2ps_red, 'red')
        match_vals[ii].append(a)
        
    match_vals[ii].sort()
    match_vals[ii] = match_vals[ii][:10]

HBox(children=(IntProgress(value=0, max=11702), HTML(value='')))

TypeError: unsupported operand type(s) for /: 'PngImageFile' and 'int'

In [40]:
l = [2,6,8,3,4]
l1 = l.sort()
l = l[:3]
print(l)

[2, 3, 4]


In [20]:
def open_rgby2(path,id): #a function that reads RGBY image
#     colors = ['red','green','blue','yellow']
    colors = ['red','green','blue']
    flags = cv2.IMREAD_GRAYSCALE
    img = [cv2.imread(os.path.join(path, id+'_'+color+'.png'), flags)
           for color in colors]
    return np.stack(img, axis=-1)

In [37]:
# p2h_red = {}
# p2h_green = {}
# p2h_blue = {}
p2h = {}
for p, l in tqdm_notebook(tagged.items()):
    pixels = open_rgby2('../data/train_combined', p)
    img = Image.fromarray(pixels.astype('uint8'), 'RGB')
    h = phash(img)
    p2h[p] = h

HBox(children=(IntProgress(value=0, max=105678), HTML(value='')))

In [45]:
p2h_test = {}
for p in tqdm_notebook(submit):
    pixels = open_rgby2('../data/test', p)
    img = Image.fromarray(pixels.astype('uint8'), 'RGB')
    h = phash(img)
    p2h_test[p] = h

HBox(children=(IntProgress(value=0, max=11702), HTML(value='')))

In [29]:
p = '00070df0-bbc3-11e8-b2bc-ac1f6b6435d0'
pixels = open_rgby2('../data/train_combined', p)

In [30]:
pixels.shape

(512, 512, 3)

In [31]:
img = Image.fromarray(pixels.astype('uint8'), 'RGB')

In [33]:
h = phash(img)

In [34]:
h

array([[ True,  True, False,  True, False,  True, False, False],
       [False,  True, False,  True, False, False, False,  True],
       [False,  True, False,  True,  True, False,  True,  True],
       [False, False, False,  True, False,  True,  True,  True],
       [False, False, False,  True, False,  True,  True, False],
       [ True,  True, False,  True, False,  True, False, False],
       [ True, False,  True,  True, False,  True,  True, False],
       [False, False,  True,  True,  True,  True, False, False]])

In [28]:
for p, l in tqdm_notebook(tagged.items()):
    print(p)

HBox(children=(IntProgress(value=0, max=105678), HTML(value='')))

00070df0-bbc3-11e8-b2bc-ac1f6b6435d0
000a6c98-bb9b-11e8-b2b9-ac1f6b6435d0
000a9596-bbc4-11e8-b2bc-ac1f6b6435d0
000c99ba-bba4-11e8-b2b9-ac1f6b6435d0
001838f8-bbca-11e8-b2bc-ac1f6b6435d0
001bcdd2-bbb2-11e8-b2ba-ac1f6b6435d0
0020af02-bbba-11e8-b2ba-ac1f6b6435d0
002679c2-bbb6-11e8-b2ba-ac1f6b6435d0
00285ce4-bba0-11e8-b2b9-ac1f6b6435d0
002daad6-bbc9-11e8-b2bc-ac1f6b6435d0
002ff91e-bbb8-11e8-b2ba-ac1f6b6435d0
00301238-bbb2-11e8-b2ba-ac1f6b6435d0
0032a07e-bba9-11e8-b2ba-ac1f6b6435d0
00344514-bbc2-11e8-b2bb-ac1f6b6435d0
00357b1e-bba9-11e8-b2ba-ac1f6b6435d0
00383b44-bbbb-11e8-b2ba-ac1f6b6435d0
0038d6a6-bb9a-11e8-b2b9-ac1f6b6435d0
003957a8-bbb7-11e8-b2ba-ac1f6b6435d0
003feb6e-bbca-11e8-b2bc-ac1f6b6435d0
0042017c-bba4-11e8-b2b9-ac1f6b6435d0
00456fd2-bb9b-11e8-b2b9-ac1f6b6435d0
0047c984-bba6-11e8-b2ba-ac1f6b6435d0
00481c70-bba3-11e8-b2b9-ac1f6b6435d0
004a2b84-bbc4-11e8-b2bc-ac1f6b6435d0
004b47de-bbca-11e8-b2bc-ac1f6b6435d0
004bf4c6-bbc6-11e8-b2bc-ac1f6b6435d0
004d8a0e-bbc4-11e8-b2bc-ac1f6b6435d0
0

1ab08f44-bbc0-11e8-b2bb-ac1f6b6435d0
1ab2ce90-bbba-11e8-b2ba-ac1f6b6435d0
1ab6e786-bba7-11e8-b2ba-ac1f6b6435d0
1ab8aa2a-bba8-11e8-b2ba-ac1f6b6435d0
1abb014a-bbb6-11e8-b2ba-ac1f6b6435d0
1abb65fe-bbbb-11e8-b2ba-ac1f6b6435d0
1ac0c25a-bbb2-11e8-b2ba-ac1f6b6435d0
1ac2966a-bbb8-11e8-b2ba-ac1f6b6435d0
1ac6613a-bbb0-11e8-b2ba-ac1f6b6435d0
1ac68314-bba5-11e8-b2ba-ac1f6b6435d0
1ac84f16-bba3-11e8-b2b9-ac1f6b6435d0
1acab3ca-bbbf-11e8-b2ba-ac1f6b6435d0
1acac716-bbab-11e8-b2ba-ac1f6b6435d0
1acbe116-bbb8-11e8-b2ba-ac1f6b6435d0
1acc61b6-bb9c-11e8-b2b9-ac1f6b6435d0
1accf152-bbb6-11e8-b2ba-ac1f6b6435d0
1acd0e30-bbc0-11e8-b2bb-ac1f6b6435d0
1acd2128-bbab-11e8-b2ba-ac1f6b6435d0
1ace612a-bbae-11e8-b2ba-ac1f6b6435d0
1acebdae-bbb9-11e8-b2ba-ac1f6b6435d0
1acfaddc-bbbd-11e8-b2ba-ac1f6b6435d0
1ad0095c-bbaa-11e8-b2ba-ac1f6b6435d0
1ad11a96-bbb3-11e8-b2ba-ac1f6b6435d0
1ad13188-bba5-11e8-b2ba-ac1f6b6435d0
1ad416ea-bbbf-11e8-b2ba-ac1f6b6435d0
1ad4744c-bbc3-11e8-b2bc-ac1f6b6435d0
1ad6c052-bbab-11e8-b2ba-ac1f6b6435d0
1

34bd809c-bbaf-11e8-b2ba-ac1f6b6435d0
34be3158-bbba-11e8-b2ba-ac1f6b6435d0
34bf9e82-bb9a-11e8-b2b9-ac1f6b6435d0
34bffe58-bba0-11e8-b2b9-ac1f6b6435d0
34c08f78-bba8-11e8-b2ba-ac1f6b6435d0
34c2cc94-bbb1-11e8-b2ba-ac1f6b6435d0
34c4aca8-bbc5-11e8-b2bc-ac1f6b6435d0
34caa79c-bba3-11e8-b2b9-ac1f6b6435d0
34cecda6-bbbf-11e8-b2ba-ac1f6b6435d0
34cf3196-bba2-11e8-b2b9-ac1f6b6435d0
34d07184-bbc8-11e8-b2bc-ac1f6b6435d0
34d1c460-bba7-11e8-b2ba-ac1f6b6435d0
34d1e77a-bba6-11e8-b2ba-ac1f6b6435d0
34d48f56-bba2-11e8-b2b9-ac1f6b6435d0
34d60e58-bbbb-11e8-b2ba-ac1f6b6435d0
34d6aae6-bb9a-11e8-b2b9-ac1f6b6435d0
34d79f24-bba8-11e8-b2ba-ac1f6b6435d0
34de991e-bbc1-11e8-b2bb-ac1f6b6435d0
34e07480-bbaa-11e8-b2ba-ac1f6b6435d0
34e291f6-bbb0-11e8-b2ba-ac1f6b6435d0
34e7d2e6-bbb6-11e8-b2ba-ac1f6b6435d0
34e86294-bbaf-11e8-b2ba-ac1f6b6435d0
34ee027e-bbac-11e8-b2ba-ac1f6b6435d0
34ee6d4c-bbbe-11e8-b2ba-ac1f6b6435d0
34f24b16-bbc2-11e8-b2bb-ac1f6b6435d0
34fa7330-bbb4-11e8-b2ba-ac1f6b6435d0
34fb01a6-bbb4-11e8-b2ba-ac1f6b6435d0
3

4da7c014-bbc7-11e8-b2bc-ac1f6b6435d0
4db05b34-bbb3-11e8-b2ba-ac1f6b6435d0
4db30bbe-bbb2-11e8-b2ba-ac1f6b6435d0
4db910fc-bbb4-11e8-b2ba-ac1f6b6435d0
4dbd79ae-bb9a-11e8-b2b9-ac1f6b6435d0
4dbf6216-bbc5-11e8-b2bc-ac1f6b6435d0
4dc066d6-bba5-11e8-b2ba-ac1f6b6435d0
4dc52d7a-bbc7-11e8-b2bc-ac1f6b6435d0
4dc69324-bbb6-11e8-b2ba-ac1f6b6435d0
4dd064dc-bba5-11e8-b2ba-ac1f6b6435d0
4dd118ce-bbb3-11e8-b2ba-ac1f6b6435d0
4dd2c90a-bbca-11e8-b2bc-ac1f6b6435d0
4dd3f9c0-bbab-11e8-b2ba-ac1f6b6435d0
4dd6f368-bbca-11e8-b2bc-ac1f6b6435d0
4dd7c974-bbc9-11e8-b2bc-ac1f6b6435d0
4dd980c0-bbba-11e8-b2ba-ac1f6b6435d0
4ddb1e84-bba2-11e8-b2b9-ac1f6b6435d0
4ddf3740-bbba-11e8-b2ba-ac1f6b6435d0
4de099fc-bb9f-11e8-b2b9-ac1f6b6435d0
4de12048-bbb3-11e8-b2ba-ac1f6b6435d0
4de1e3d2-bbbf-11e8-b2ba-ac1f6b6435d0
4de539f8-bbc7-11e8-b2bc-ac1f6b6435d0
4de87e5a-bba0-11e8-b2b9-ac1f6b6435d0
4de8e49c-bbc5-11e8-b2bc-ac1f6b6435d0
4de8f0da-bbb2-11e8-b2ba-ac1f6b6435d0
4de96dd2-bbb5-11e8-b2ba-ac1f6b6435d0
4dea5c08-bba9-11e8-b2ba-ac1f6b6435d0
4

...

47872_1303_F7_4
47872_1511_C7_1
47872_1511_C7_4
47872_1753_F7_18_cr57f3e8e464164
47872_1753_F7_28_cr57f3e8ef1ec4c
44560_555_D11_2
44560_555_D11_3
44560_504_D11_1
44560_504_D11_2
44560_506_D11_1
44560_506_D11_2
30796_373_H3_1
30796_373_H3_2
30796_370_H3_1
30796_370_H3_2
65785_1591_G11_2
65785_1591_G11_5
65785_1283_C9_1
65785_1283_C9_2
65785_1286_C9_1
65785_1286_C9_2
36492_407_B7_1
36492_407_B7_2
36492_410_B7_1
36492_410_B7_2
36492_404_B7_1
36492_404_B7_2
48786_900_F12_1
48786_900_F12_2
48786_858_E6_1
48786_858_E6_3
48786_850_E6_3
48786_850_E6_4
26836_1265_B1_2
26836_1265_B1_3
26836_1276_B9_1
26836_1276_B9_3
26836_1274_B1_2
26836_1274_B1_3
54110_885_A1_1
54110_885_A1_2
54110_869_A1_1
54110_869_A1_2
54110_849_A1_1
54110_849_A1_2
18168_144_F3_1
18168_144_F3_2
18168_145_F3_1
18168_145_F3_2
18168_143_F3_1
18168_143_F3_2
73690_1786_H5_2
73690_1786_H5_6
73690_1721_G3_8_cr57eaae0c1640a
73690_1721_G3_18_cr57eaae14981b2
73690_1617_G3_1
73690_1617_G3_2
36471_434_D3_3
36471_434_D3_4
36471_453_D3_1


44991_575_H6_1
44991_575_H6_2
44991_568_H6_1
44991_568_H6_2
11384_108_B11_1
11384_108_B11_2
11384_87_B11_1
11384_87_B11_2
11384_85_B11_1
11384_85_B11_2
12983_674_C10_1
12983_674_C10_2
12983_668_C10_6
12983_668_C10_8
12983_665_C10_1
12983_665_C10_2
595_54_E7_1
595_54_E7_2
595_53_E7_1
595_53_E7_2
595_55_E7_1
595_55_E7_2
37949_592_A10_1
37949_592_A10_3
37949_1081_H11_1
37949_1081_H11_2
37949_582_A10_1
37949_582_A10_2
12226_617_E2_1
12226_617_E2_2
12226_613_E2_3
12226_613_E2_4
12226_610_E2_1
12226_610_E2_3
16388_946_A9_1
16388_946_A9_2
16388_945_A9_1
16388_945_A9_2
16388_953_A9_1
16388_953_A9_3
21563_147_D9_1
21563_147_D9_2
21563_148_D9_1
21563_148_D9_2
21563_146_D9_1
21563_146_D9_2
53012_826_F5_1
53012_826_F5_2
53012_809_F5_1
53012_809_F5_2
53012_819_F5_1
53012_819_F5_2
53012_926_F7_2
53012_926_F7_3
15633_128_F1_1
15633_128_F1_2
15633_129_F1_1
15633_129_F1_2
15633_127_F1_1
15633_127_F1_2
15984_128_A9_1
15984_128_A9_2
15984_129_A9_1
15984_129_A9_2
15984_127_A9_1
15984_127_A9_2
74432_1668_F

29579_364_B12_2
73667_1576_A8_1
73667_1576_A8_2
73667_1486_C7_1
73667_1486_C7_5
16579_1124_H2_1
16579_1124_H2_2
16579_280_B4_1
16579_280_B4_2
59374_1043_E5_1
59374_1043_E5_3
59374_1014_F5_1
59374_1014_F5_2
59374_1010_F5_1
59374_1010_F5_2
47860_1004_B8_1
47860_1004_B8_2
47860_1002_B8_1
47860_1002_B8_2
60310_1227_H4_1
60310_1227_H4_2
60310_1271_H4_2
60310_1271_H4_3
30059_296_C4_1
30059_296_C4_2
30059_297_C4_1
30059_297_C4_2
30059_295_C4_1
30059_295_C4_2
44380_608_D10_1
44380_608_D10_2
44380_606_D10_1
44380_606_D10_2
44380_605_D10_2
44380_605_D10_3
52865_1011_G2_3
52865_1011_G2_9
52865_1319_E6_1
52865_1319_E6_2
52865_1006_G2_1
52865_1006_G2_2
3097_54_A2_1
3097_54_A2_2
3097_53_A2_1
3097_53_A2_2
3097_55_A2_1
3097_55_A2_2
5385_639_D4_3
5385_639_D4_4
5385_635_D4_1
5385_635_D4_3
5385_634_D4_1
5385_634_D4_2
3302_72_F1_1
3302_72_F1_2
3302_73_F1_1
3302_73_F1_2
3302_71_F1_1
3302_71_F1_2
31997_1253_B6_1
31997_1253_B6_4
31997_1134_C11_1
31997_1134_C11_2
57346_1259_E4_6
57346_1259_E4_8
57346_1076_G7_

37677_441_A2_1
37677_441_A2_2
37677_432_A2_1
37677_432_A2_3
37677_430_A2_1
37677_430_A2_2
37677_si30_E4_1
37677_si30_E4_3
37677_si30_E4_11
37677_si30_E4_16
37677_si30_E6_1
37677_si30_E6_4
37677_si30_E6_7
37677_si30_E6_20
37678_608_H5_1
37678_608_H5_2
37678_606_H5_1
37678_606_H5_2
37678_605_H5_1
37678_605_H5_2
23447_216_C4_1
23447_216_C4_2
23447_217_C4_2
23447_217_C4_1
23447_215_C4_1
23447_215_C4_2
23571_226_D1_1
23571_226_D1_2
23571_si25_G10_2
23571_si25_G10_3
23571_si25_G10_9
23571_si25_G10_15
23571_si25_G12_1
23571_si25_G12_2
23571_si25_G12_15
23571_si25_G12_20
25941_394_G8_1
25941_394_G8_2
25941_395_G8_2
25941_395_G8_4
25941_399_G8_1
25941_399_G8_2
46085_1663_E4_2
46085_1663_E4_3
57905_1301_H6_6
57905_1301_H6_7
40290_487_H1_1
40290_487_H1_2
40290_1129_E4_1
40290_1129_E4_2
40290_491_H1_1
40290_491_H1_2
28276_285_A11_1
28276_285_A11_2
28276_286_A11_4
28276_286_A11_5
28276_284_A11_2
28276_284_A11_1
40720_547_E1_1
40720_547_E1_2
40720_532_E1_1
40720_532_E1_2
40720_496_E1_1
40720_496_E1_

43279_494_B6_1
43279_494_B6_2
43279_485_B6_4
43279_485_B6_5
60103_1520_G10_1
60103_1520_G10_2
60103_1335_G5_1
60103_1335_G5_2
60103_1352_G5_1
60103_1352_G5_2
71699_1411_A5_5
71699_1411_A5_6
71699_1374_A10_1
71699_1374_A10_2
71699_1376_A10_1
71699_1376_A10_3
48922_714_G7_1
48922_714_G7_2
48922_713_G7_1
48922_713_G7_2
67288_1284_F9_1
67288_1284_F9_2
67288_1217_A11_1
67288_1217_A11_2
67288_1211_A11_1
67288_1211_A11_3
28457_1520_A12_1
28457_1520_A12_2
28457_1466_A7_3
28457_1466_A7_4
28457_1521_A7_1
28457_1521_A7_3
73186_1475_C2_3
73186_1475_C2_5
73186_1412_D2_1
73186_1412_D2_2
73186_1409_D2_1
73186_1409_D2_2
30335_1337_C12_1
30335_1337_C12_3
30335_1338_C12_1
30335_1338_C12_2
67970_1581_F9_3
67970_1581_F9_4
67970_1374_D5_1
67970_1374_D5_2
67970_1376_D5_2
67970_1376_D5_3
78322_1702_C6_31
78322_1702_C6_32
78322_1767_H6_14_cr594a8cec9cdda
78322_1767_H6_28_cr595e4d456ccf1
78322_1706_F8_32
78322_1706_F8_33
55007_1182_E5_2
55007_1182_E5_4
55007_1638_H1_1
55007_1638_H1_2
55007_966_D3_1
55007_966_D

In [39]:
# Find all images associated with a given phash value.
h2ps = {}
for p,h in tqdm_notebook(p2h.items()):
    if h not in h2ps: h2ps[h] = []
    if p not in h2ps: h2ps[h].append(p)

# Find all distinct phash values
hs = list(h2ps.keys())

HBox(children=(IntProgress(value=0, max=105678), HTML(value='')))

In [46]:
for p,h in tqdm_notebook(p2h_test.items()):
    if h not in h2ps: h2ps[h] = []
    if p not in h2ps: h2ps[h].append(p)


HBox(children=(IntProgress(value=0, max=11702), HTML(value='')))

In [52]:
fp_train = np.memmap('../cache/train_pics', dtype=np.float32, mode='w+', shape=(105678, 512,512,3))


In [62]:
fp_test = np.memmap('../cache/test_pics', dtype=np.float32, mode='w+', shape=(len(submit), 512,512,3))

In [53]:
for idx, p in tqdm_notebook(enumerate(tagged)):
    img =  open_rgby2('../data/train_combined', p)
    fp_train[idx] = img

HBox(children=(IntProgress(value=1, bar_style='info', max=1), HTML(value='')))

In [60]:
len(submit)

11702

In [63]:
for idx, p in tqdm_notebook(enumerate(submit)):
    img =  open_rgby2('../data/test', p)
    fp_test[idx] = img

HBox(children=(IntProgress(value=1, bar_style='info', max=1), HTML(value='')))

In [ ]:
# with open('../cache/h2ps.pkl', 'wb') as f:
#     pickle.dump(h2ps, f)
# with open('../cache/p2h.pkl', 'wb') as f:
#     pickle.dump(p2h, f)
# with open('../cache/p2h_test.pkl', 'wb') as f:
#     pickle.dump(p2h_test, f)

In [15]:
import pickle
with open('../cache/h2ps.pkl', 'rb') as f:
    h2ps = pickle.load(f)
with open('../cache/p2h.pkl', 'rb') as f:
    p2h = pickle.load(f)
with open('../cache/p2h_test.pkl', 'rb') as f:
    p2h_test = pickle.load(f)

In [16]:
X_train = np.memmap('../cache/train_pics', mode='r', dtype=np.float32)
X_test = np.memmap('../cache/test_pics', mode='r', dtype=np.float32)

In [17]:
submit[0]

'00008af0-bad0-11e8-b2b8-ac1f6b6435d0'

In [18]:
submit.index('00008af0-bad0-11e8-b2b8-ac1f6b6435d0')

0

In [19]:
t_k = list(tagged.keys())
t_k[0]

'00070df0-bbc3-11e8-b2bc-ac1f6b6435d0'

In [20]:
t_k.index('00070df0-bbc3-11e8-b2bc-ac1f6b6435d0')

0

In [21]:
from math import sqrt
def match2(h1,h2, h2ps):
    for p1 in h2ps[h1]:
        idx1 = submit.index(p1)
        b = X_test[idx1]
        a1 = b - b.mean()
        a1 = a1/sqrt((a1**2).mean())
        for p2 in h2ps[h2]:
#             a1 =  open_rgby2('../data/test', p1)
#             a2 =  open_rgby2('../data/train_combined', p2)
#             if i1.mode != i2.mode or i1.size != i2.size: return False
#             a1 = np.array(i1)
            idx2 = t_k.index(p2)
            
#             a2 = np.array(i2)
            a2 = X_train[idx2]
            a2 = a2 - a2.mean()
            a2 = a2/sqrt((a2**2).mean())
            a  = ((a1 - a2)**2).mean()
#             if a > 0.1: return False
#             if a > 1.0: return False
            return a
    return 9999.0

In [22]:
from multiprocessing import Pool

match_vals = {}
def get_similar_pics(ii):
    h1 = p2h_test[ii]
    match_vals[ii] = []
    for jj in tagged:
        h2 = p2h[jj]
        a = match2(h1, h2, h2ps)
        match_vals[ii].append(a)
        
    match_vals[ii].sort()
    match_vals[ii] = match_vals[ii][:10]
    name = '../cache/pkl/{}.pkl'.format(ii)
    with open(name, 'wb') as f:
        pickle.dump(match_vals[ii], f)

In [23]:
pool = Pool(processes=20)
params = [p for p in submit]
# pool.map( get_similar_pics, params )

/home/watts/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in true_divide
  import sys
/home/watts/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in true_divide
  import sys
/home/watts/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in true_divide
  import sys
/home/watts/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:18: RuntimeWarning: invalid value encountered in true_divide
/home/watts/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in true_divide
  import sys
/home/watts/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:18: RuntimeWarning: invalid value encountered in true_divide
/home/watts/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:7: RuntimeWarning: invalid value encountered in true_divide
  import sys
/home/wat

In [ ]:
# for i, _ in enumerate(pool.imap_unordered(get_similar_pics, params), 1):
#     print('\rdone {0:%}'.format(i/20))
from os.path import isfile
from PIL import Image as pil_image
from tqdm import tqdm_notebook

for _ in tqdm_notebook(pool.imap_unordered(get_similar_pics, params), total=20):
    pass

HBox(children=(IntProgress(value=0, max=20), HTML(value='')))

In [76]:
# match_vals = {}
# for ii in tqdm_notebook(submit):
#     h1 = p2h_test[ii]
#     match_vals[ii] = []
#     for jj in tqdm_notebook(tagged):
#         h2 = p2h[jj]
#         a = match2(h1, h2, h2ps)
#         match_vals[ii].append(a)
        
#     match_vals[ii].sort()
#     match_vals[ii] = match_vals[ii][:10]